In [1]:
!pip install sktime

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.5/17.5 MB 88.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.7/118.7 kB 17.3 MB/s eta 0:00:00


In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
import pandas as pd
import numpy as np
import torch
from tqdm.auto import tqdm
import random
import os

def reset_seeds(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True

DATA_PATH = '/content/drive/MyDrive/데이콘 캐글 컴페티션/DACON_23.07_PowerConsumption/'
SEED = 42

device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

In [4]:
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
import sktime
from sktime.forecasting.model_selection import temporal_train_test_split
from sktime.utils.plotting import plot_series
import matplotlib.pyplot as pl24
from sklearn.metrics import make_scorer
from lightgbm import early_stopping
import xgboost as xgb
import seaborn as sns

In [5]:
def _smape(true, pred):
    true = np.array(true)
    pred = np.array(pred)
    v = 2 * np.abs(pred - true) / (np.abs(pred) + np.abs(true))
    output = np.mean(v) * 100
    return output
smape = make_scorer(_smape, greater_is_better=False)


def lightgbm_smape(y_true, y_pred):
    smape_val = _smape(y_true, y_pred)
    return 'SMAPE', smape_val, False

In [6]:
train = pd.read_csv(f"{DATA_PATH}train.csv")
test = pd.read_csv(f"{DATA_PATH}test.csv")
# building = pd.read_csv(f"{DATA_PATH}building_info.csv")
submission = pd.read_csv(f"{DATA_PATH}sample_submission.csv")

In [7]:

train_ft = pd.read_csv(f'{DATA_PATH}train_ver3.csv') #ver 4 미완성본

test_ft = pd.read_csv(f'{DATA_PATH}test_ver3.csv')


# train_ft = pd.read_csv(f'{DATA_PATH}train_ver5.2_ys.csv') #ver 4 미완성본

# test_ft = pd.read_csv(f'{DATA_PATH}test_ver5.2_ys.csv')

# train_ft = pd.read_csv(f"{DATA_PATH}train_feature9.csv")
# test_ft = pd.read_csv(f"{DATA_PATH}test_feature9.csv")


# train_ft = pd.read_csv(f"{DATA_PATH}train_selected_3.csv")
# test_ft = pd.read_csv(f"{DATA_PATH}test_selected_3.csv")

# df = pd.read_csv(f"{DATA_PATH}train_featured_3.csv")


In [8]:
# cols = ['day_hour_mean', 'day_hour_median', 'discomfort_CDH', 'week',
#        'day_hour_mode', 'discomfort', 'day_hour_std', 'CDH', 'hour_mean',
#        'sin_time', 'cos_week','building_num','energy_consum']

# train_ft = df[cols]

- 피처추가

In [9]:
train_ft.shape, test_ft.shape

((201600, 31), (16800, 28))

In [10]:
train_ft.columns

cols = ['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind', 'hum',
       'sunshine', 'solar_rad', 'building_type', 'time', 'day', 'month', 'week',
       'day_of_year', 'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM',
       'temp_EMA', 'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH',
       'hour_mean', 'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave']


train_ft.columns = cols

In [11]:
test_ft.columns

cols = ['building_num', 'date_time', 'temp', 'precip', 'wind', 'hum', 'building_type',
       'time', 'day', 'month', 'week', 'day_of_year', 'sin_time', 'cos_time',
       'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA', 'wind_EMA', 'hum_EMA',
       'THI', 'feels_temp', 'CDH', 'hour_mean', 'day_hour_mean', 'hour_std',
       'heat_index', 'heat_wave']

test_ft.columns = cols

In [12]:
train_ft.isna().sum().sum(), test_ft.isna().sum().sum()

(0, 0)

In [13]:
train_ft.shape, test_ft.shape

((201600, 31), (16800, 28))

In [14]:
cols = ['sunshine', 'solar_rad']
train_ft = train_ft.drop(columns=cols)

요일별 6시간 전 대비 전력 변화율

In [15]:
train_ft.day

0         3
1         3
2         3
3         3
4         3
         ..
201595    2
201596    2
201597    2
201598    2
201599    2
Name: day, Length: 201600, dtype: int64

In [16]:
# train_ft['power_change_rate'] = (train_ft['energy_consum'] - train_ft.groupby(['building_num', train_ft.day])['energy_consum'].shift(6)) / train_ft.groupby(['building_num', train_ft.day])['energy_consum'].shift(6)


In [17]:
# train_ft['day_within_cycle'] = train_ft.index % (7*24)

# periodic_avg_power_change_rate = train_ft.groupby(['building_num', 'day_within_cycle'])['power_change_rate'].mean().reset_index()
# periodic_avg_power_change_rate.rename(columns={'power_change_rate': 'periodic_avg_power_change_rate'}, inplace=True)

# train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num', 'day_within_cycle'], how='left')

In [18]:
# cols = ['day_within_cycle', 'power_change_rate']
# train_ft = train_ft.drop(columns=cols)

# train_ft['periodic_avg_power_change_rate'].nunique()

# last_rows = train_ft.groupby('building_num').tail(28)['periodic_avg_power_change_rate'].reset_index().drop('index', axis=1)
# test_ft = pd.concat([test_ft, last_rows], axis=1)

In [19]:
# train_ft['power_change_rate'] = (train_ft['energy_consum'] - train_ft.groupby(['building_num', train_ft.day])['energy_consum'].shift(6)) / train_ft.groupby(['building_num', train_ft.day])['energy_consum'].shift(6)

# train_ft['day_within_cycle'] = train_ft.index % (7*24)

# periodic_avg_power_change_rate = train_ft.groupby(['building_num', 'day_within_cycle'])['power_change_rate'].mean().reset_index()
# periodic_avg_power_change_rate.rename(columns={'power_change_rate': 'periodic_avg_power_change_rate'}, inplace=True)

# train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num', 'day_within_cycle'], how='left')

# cols = ['day_within_cycle', 'power_change_rate']
# train_ft = train_ft.drop(columns=cols)

# train_ft['periodic_avg_power_change_rate'].nunique()

# last_rows = train_ft.groupby('building_num').tail(28)['periodic_avg_power_change_rate'].reset_index().drop('index', axis=1)
# test_ft = pd.concat([test_ft, last_rows], axis=1)


In [20]:
train_ft.columns

Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave'],
      dtype='object')

#

In [21]:
# train_ft['day_hour_mean_log'] = train_ft['day_hour_mean'].apply(np.log)
# test_ft['day_hour_mean_log'] = test_ft['day_hour_mean'].apply(np.log)

In [22]:
# time_intervals = pd.cut(train_ft['time'], bins=[0, 6, 12, 18, 24], labels=['00-06', '06-12', '12-18', '18-24'])

# # Group data by building_num, day, and time intervals, and calculate the cumulative mean day hour mean
# train_ft['building_day_time_cummean'] = train_ft.groupby(['building_num', 'day', time_intervals])['day_hour_mean'].cumsum()

In [23]:
# train_ft['building_day_time_cummean']

In [24]:
# time_intervals = pd.cut(test_ft['time'], bins=[0, 6, 12, 18, 24], labels=['00-06', '06-12', '12-18', '18-24'])

# # Group data by building_num, day, and time intervals, and calculate the cumulative mean day hour mean
# test_ft['building_day_time_cummean'] = test_ft.groupby(['building_num', 'day', time_intervals])['day_hour_mean'].cumsum()

In [25]:
train_ft.columns

Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave'],
      dtype='object')

In [26]:
train_ft['temp_EMA']

0         22.027950
1         21.346727
2         20.708769
3         20.168959
4         19.712196
            ...    
201595    24.273233
201596    23.985044
201597    23.571960
201598    23.176274
201599    22.795309
Name: temp_EMA, Length: 201600, dtype: float64

- 기온의 제곱값

In [27]:
train_ft['temp_2'] = train_ft['temp']**2
test_ft['temp_2'] = test_ft['temp']**2


- month week hour

In [28]:
# week : day hour mean의 7일치 평균



In [29]:
# month_week_hour_mean = pd.pivot_table(train_ft, values = 'energy_consum', index = ['building_num', 'month','week','time'], aggfunc = np.mean).reset_index()
# month_week_hour_mean.rename(columns={'energy_consum': 'month_week_hour_mean'}, inplace=True)

# train_ft = train_ft.merge(month_week_hour_mean, on=['building_num', 'month','week','time'], how='left')

# test_ft = test_ft.merge(month_week_hour_mean, on=['building_num', 'month','week','time'], how='left')

In [30]:
# test_ft.merge(month_week_hour_mean, on=['building_num', 'month','week','time'], how='left')

In [31]:
train_ft.isnull().sum().sum(), test_ft.isnull().sum().sum()

(0, 0)


7일 주기, 7일전 대비 전력 변화율

In [32]:
train_ft['day_hour_mean'].nunique() # 168개 고유값. 건물별로.

16425

In [33]:
train_ft

energy_consum  building_num    date_time  temp  precip  wind   hum  \
0             1034.40             1  20220602 00  18.1     0.0   0.4  67.0   
1              973.92             1  20220602 01  17.6     0.0   0.8  69.0   
2              909.12             1  20220602 02  17.2     0.0   0.7  71.0   
3              893.28             1  20220602 03  17.2     0.0   2.2  75.0   
4              924.00             1  20220602 04  17.2     0.0   2.0  81.0   
...               ...           ...          ...   ...     ...   ...   ...   
201595         881.04           100  20220824 19  23.1     0.0   0.9  86.0   
201596         798.96           100  20220824 20  22.4     0.0   1.3  86.0   
201597         825.12           100  20220824 21  21.3     0.0   1.0  92.0   
201598         640.08           100  20220824 22  21.0     0.0   0.3  94.0   
201599         540.24           100  20220824 23  20.7     0.0   0.1  95.0   

       building_type  time  day  ...    hum_EMA        THI  feels_temp  \
0               건물기타     0    3  ...  47.470422  69.672872   28.818026   
1               건물기타     1    3  ...  50.782665  68.942223   27.987268   
2               건물기타     2    3  ...  53.893024  68.121589   27.080175   
3               건물기타     3    3  ...  57.140251  67.254888   26.152269   
4               건물기타     4    3  ...  60.810982  66.367960   25.248724   
...              ...   ...  ...  ...        ...        ...         ...   
201595        호텔및리조트    19    2  ...  79.956781  73.846285   30.510262   
201596        호텔및리조트    20    2  ...  80.886507  73.733854   30.441848   
201597        호텔및리조트    21    2  ...  82.596275  73.494949   30.233938   
201598        호텔및리조트    22    2  ...  84.350694  73.192381   29.960151   
201599        호텔및리조트    23    2  ...  85.989049  72.851867   29.663653   

              CDH    hour_mean  day_hour_mean    hour_std  heat_index  \
0       -1.850000  1713.711429        1627.80  444.306331         0.0   
1       -4.591667  1629.468571        1550.08  437.718795         0.0   
2       -8.266667  1513.305714        1431.12  410.362488         0.0   
3      -12.866667  1443.122857        1372.20  389.916262         0.0   
4      -18.333333  1452.808571        1381.72  379.995696         0.0   
...           ...          ...            ...         ...         ...   
201595 -35.641667  1012.602857         976.06  161.150392         0.0   
201596 -33.391667   930.205714         892.92  137.040302         0.0   
201597 -31.266667   831.714286         786.62  128.125250         0.0   
201598 -29.483333   724.480000         667.94  112.413470         0.0   
201599 -28.083333   589.820000         566.94   91.531822         0.0   

        heat_wave  temp_2  
0               0  327.61  
1               0  309.76  
2               0  295.84  
3               0  295.84  
4               0  295.84  
...           ...     ...  
201595          0  533.61  
201596          0  501.76  
201597          0  453.69  
201598          0  441.00  
201599          0  428.49  

[201600 rows x 30 columns]

In [34]:
train_ft['power_change_rate'] = (train_ft['energy_consum'] - train_ft.groupby('building_num')['energy_consum'].shift(7*24)) / train_ft.groupby('building_num')['energy_consum'].shift(7*24)

train_ft['day_within_cycle'] = train_ft.index % (7*24)

periodic_avg_power_change_rate = train_ft.groupby(['building_num','day_within_cycle' ])['power_change_rate'].mean().reset_index()
periodic_avg_power_change_rate.rename(columns={'power_change_rate': 'periodic_avg_power_change_rate'}, inplace=True)

train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num','day_within_cycle'], how='left')
cols = ['day_within_cycle','power_change_rate']
train_ft = train_ft.drop(columns = cols)

train_ft['periodic_avg_power_change_rate'].nunique()

last_rows = train_ft.groupby('building_num').tail(168)['periodic_avg_power_change_rate'].reset_index().drop('index',axis=1)
test_ft = pd.concat([test_ft, last_rows], axis=1)

In [35]:
train_ft['power_change_rate_6'] = (train_ft['energy_consum'] - train_ft.groupby('building_num')['energy_consum'].shift(24)) / train_ft.groupby('building_num')['energy_consum'].shift(24)

train_ft['day_within_cycle_6'] = train_ft.index % (24)

periodic_avg_power_change_rate = train_ft.groupby(['building_num','day_within_cycle_6' ])['power_change_rate_6'].mean().reset_index()
periodic_avg_power_change_rate.rename(columns={'power_change_rate_6': 'periodic_avg_power_change_rate_6'}, inplace=True)

train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num','day_within_cycle_6'], how='left')
cols = ['day_within_cycle_6','power_change_rate_6']
train_ft = train_ft.drop(columns = cols)

train_ft['periodic_avg_power_change_rate_6'].nunique()

last_rows = train_ft.groupby('building_num').tail(168)['periodic_avg_power_change_rate_6'].reset_index().drop('index',axis=1)
test_ft = pd.concat([test_ft, last_rows], axis=1)

In [36]:
train_ft['week']

0         22
1         22
2         22
3         22
4         22
          ..
201595    34
201596    34
201597    34
201598    34
201599    34
Name: week, Length: 201600, dtype: int64

In [37]:
train_ft['day']

0         3
1         3
2         3
3         3
4         3
         ..
201595    2
201596    2
201597    2
201598    2
201599    2
Name: day, Length: 201600, dtype: int64

In [38]:
train_ft

energy_consum  building_num    date_time  temp  precip  wind   hum  \
0             1034.40             1  20220602 00  18.1     0.0   0.4  67.0   
1              973.92             1  20220602 01  17.6     0.0   0.8  69.0   
2              909.12             1  20220602 02  17.2     0.0   0.7  71.0   
3              893.28             1  20220602 03  17.2     0.0   2.2  75.0   
4              924.00             1  20220602 04  17.2     0.0   2.0  81.0   
...               ...           ...          ...   ...     ...   ...   ...   
201595         881.04           100  20220824 19  23.1     0.0   0.9  86.0   
201596         798.96           100  20220824 20  22.4     0.0   1.3  86.0   
201597         825.12           100  20220824 21  21.3     0.0   1.0  92.0   
201598         640.08           100  20220824 22  21.0     0.0   0.3  94.0   
201599         540.24           100  20220824 23  20.7     0.0   0.1  95.0   

       building_type  time  day  ...  feels_temp        CDH    hour_mean  \
0               건물기타     0    3  ...   28.818026  -1.850000  1713.711429   
1               건물기타     1    3  ...   27.987268  -4.591667  1629.468571   
2               건물기타     2    3  ...   27.080175  -8.266667  1513.305714   
3               건물기타     3    3  ...   26.152269 -12.866667  1443.122857   
4               건물기타     4    3  ...   25.248724 -18.333333  1452.808571   
...              ...   ...  ...  ...         ...        ...          ...   
201595        호텔및리조트    19    2  ...   30.510262 -35.641667  1012.602857   
201596        호텔및리조트    20    2  ...   30.441848 -33.391667   930.205714   
201597        호텔및리조트    21    2  ...   30.233938 -31.266667   831.714286   
201598        호텔및리조트    22    2  ...   29.960151 -29.483333   724.480000   
201599        호텔및리조트    23    2  ...   29.663653 -28.083333   589.820000   

        day_hour_mean    hour_std  heat_index  heat_wave  temp_2  \
0             1627.80  444.306331         0.0          0  327.61   
1             1550.08  437.718795         0.0          0  309.76   
2             1431.12  410.362488         0.0          0  295.84   
3             1372.20  389.916262         0.0          0  295.84   
4             1381.72  379.995696         0.0          0  295.84   
...               ...         ...         ...        ...     ...   
201595         976.06  161.150392         0.0          0  533.61   
201596         892.92  137.040302         0.0          0  501.76   
201597         786.62  128.125250         0.0          0  453.69   
201598         667.94  112.413470         0.0          0  441.00   
201599         566.94   91.531822         0.0          0  428.49   

        periodic_avg_power_change_rate  periodic_avg_power_change_rate_6  
0                             0.069171                          0.021710  
1                             0.072765                          0.023154  
2                             0.071155                          0.025346  
3                             0.067707                          0.030905  
4                             0.063264                          0.033128  
...                                ...                               ...  
201595                        0.039282                          0.004240  
201596                        0.040570                          0.004927  
201597                        0.053521                          0.006987  
201598                        0.036985                          0.008615  
201599                        0.047592                          0.007734  

[201600 rows x 32 columns]

In [39]:
train_ft['temp'].isnull().sum().sum(), train_ft['energy_consum'].isnull().sum().sum(),

(0, 0)

In [40]:
# def second_derivative(x, y):
#     dy = np.diff(y)
#     dx = np.diff(x)
#     dy_dx = dy / dx
#     d2y_dx2 = np.diff(dy_dx) / dx[1:]
#     return d2y_dx2



In [41]:
# def get_week_hour_mean(row):
#     power_mean = pd.pivot_table(train_ft, values = 'energy_consum', index = ['building_num', 'time', 'week'], aggfunc = np.mean).reset_index()

#     condition = (power_mean.building_num == row['building_num']) & \
#                 (power_mean.time == row['time']) & \
#                 (power_mean.week == row['week'])

#     matching_data = power_mean.loc[condition, 'energy_consum']

#     if not matching_data.empty:
#         return matching_data.values[0]
#     else:
#         return None

# train_ft['week_hour_mean'] = train_ft.apply(get_week_hour_mean, axis=1)
# test_ft['week_hour_mean'] = test_ft.apply(get_week_hour_mean, axis=1)

In [42]:
# # 요일별 시간별 전력량 평균 추가
# power_mean = pd.pivot_table(train_ft, values = 'energy_consum', index = ['building_num', 'time', 'week'], aggfunc = np.mean).reset_index()

# train_ft['week_hour_mean'] = train_ft.apply(lambda x : power_mean.loc[(power_mean.building_num == x['building_num']) & (power_mean.time == x['time']) & (power_mean.week == x['week']) ,'energy_consum'].values[0], axis = 1)
# test_ft['week_hour_mean'] = test_ft.apply(lambda x : power_mean.loc[(power_mean.building_num == x['building_num']) & (power_mean.time == x['time']) & (power_mean.week == x['week']) ,'energy_consum'].values[0], axis = 1)



In [43]:
pd.DataFrame(train_ft['periodic_avg_power_change_rate_6'])

periodic_avg_power_change_rate_6
0                               0.021710
1                               0.023154
2                               0.025346
3                               0.030905
4                               0.033128
...                                  ...
201595                          0.004240
201596                          0.004927
201597                          0.006987
201598                          0.008615
201599                          0.007734

[201600 rows x 1 columns]

- 건물별 요일별 시간별 표준편차 (기온, 풍속의 곱)
--> 기온이 평균과 멀어질수록. 풍속이 평균과 멀어질수록.?

In [44]:
# # 요일별 시간별 전력량 평균 추가
# wind_day_hour_std = pd.pivot_table(train_ft, values = 'wind_RM', index = ['building_num', 'time', 'day'], aggfunc = np.std).reset_index()

# train_ft['wind_day_hour_std'] = train_ft.apply(lambda x : wind_day_hour_std.loc[(wind_day_hour_std.building_num == x['building_num']) & (wind_day_hour_std.time == x['time']) & (wind_day_hour_std.day == x['day']) ,'wind_RM'].values[0], axis = 1)
# test_ft['wind_day_hour_std'] = test_ft.apply(lambda x : wind_day_hour_std.loc[(wind_day_hour_std.building_num == x['building_num']) & (wind_day_hour_std.time == x['time']) & (wind_day_hour_std.day == x['day']) ,'wind_RM'].values[0], axis = 1)

In [45]:
# train_ft['power_change_rate'] = (train_ft['energy_consum'] - train_ft.groupby('building_num')['energy_consum'].shift(6)) / train_ft.groupby('building_num')['energy_consum'].shift(6)

# train_ft['day_within_cycle'] = train_ft.index % (6)

# periodic_avg_power_change_rate = train_ft.groupby(['building_num','day_within_cycle' ])['power_change_rate'].mean().reset_index()
# periodic_avg_power_change_rate.rename(columns={'power_change_rate': 'periodic_avg_power_change_rate_6h'}, inplace=True)

# train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num','day_within_cycle'], how='left')
# cols = ['day_within_cycle','periodic_avg_power_change_rate_6h']
# train_ft = train_ft.drop(columns = cols)

# # train_ft['periodic_avg_power_change_rate_6h'].nunique()

# last_rows = train_ft.groupby('building_num').tail(168)['periodic_avg_power_change_rate_6h'].reset_index().drop('index',axis=1)
# test_ft = pd.concat([test_ft, last_rows], axis=1)

In [46]:
train_ft

energy_consum  building_num    date_time  temp  precip  wind   hum  \
0             1034.40             1  20220602 00  18.1     0.0   0.4  67.0   
1              973.92             1  20220602 01  17.6     0.0   0.8  69.0   
2              909.12             1  20220602 02  17.2     0.0   0.7  71.0   
3              893.28             1  20220602 03  17.2     0.0   2.2  75.0   
4              924.00             1  20220602 04  17.2     0.0   2.0  81.0   
...               ...           ...          ...   ...     ...   ...   ...   
201595         881.04           100  20220824 19  23.1     0.0   0.9  86.0   
201596         798.96           100  20220824 20  22.4     0.0   1.3  86.0   
201597         825.12           100  20220824 21  21.3     0.0   1.0  92.0   
201598         640.08           100  20220824 22  21.0     0.0   0.3  94.0   
201599         540.24           100  20220824 23  20.7     0.0   0.1  95.0   

       building_type  time  day  ...  feels_temp        CDH    hour_mean  \
0               건물기타     0    3  ...   28.818026  -1.850000  1713.711429   
1               건물기타     1    3  ...   27.987268  -4.591667  1629.468571   
2               건물기타     2    3  ...   27.080175  -8.266667  1513.305714   
3               건물기타     3    3  ...   26.152269 -12.866667  1443.122857   
4               건물기타     4    3  ...   25.248724 -18.333333  1452.808571   
...              ...   ...  ...  ...         ...        ...          ...   
201595        호텔및리조트    19    2  ...   30.510262 -35.641667  1012.602857   
201596        호텔및리조트    20    2  ...   30.441848 -33.391667   930.205714   
201597        호텔및리조트    21    2  ...   30.233938 -31.266667   831.714286   
201598        호텔및리조트    22    2  ...   29.960151 -29.483333   724.480000   
201599        호텔및리조트    23    2  ...   29.663653 -28.083333   589.820000   

        day_hour_mean    hour_std  heat_index  heat_wave  temp_2  \
0             1627.80  444.306331         0.0          0  327.61   
1             1550.08  437.718795         0.0          0  309.76   
2             1431.12  410.362488         0.0          0  295.84   
3             1372.20  389.916262         0.0          0  295.84   
4             1381.72  379.995696         0.0          0  295.84   
...               ...         ...         ...        ...     ...   
201595         976.06  161.150392         0.0          0  533.61   
201596         892.92  137.040302         0.0          0  501.76   
201597         786.62  128.125250         0.0          0  453.69   
201598         667.94  112.413470         0.0          0  441.00   
201599         566.94   91.531822         0.0          0  428.49   

        periodic_avg_power_change_rate  periodic_avg_power_change_rate_6  
0                             0.069171                          0.021710  
1                             0.072765                          0.023154  
2                             0.071155                          0.025346  
3                             0.067707                          0.030905  
4                             0.063264                          0.033128  
...                                ...                               ...  
201595                        0.039282                          0.004240  
201596                        0.040570                          0.004927  
201597                        0.053521                          0.006987  
201598                        0.036985                          0.008615  
201599                        0.047592                          0.007734  

[201600 rows x 32 columns]

일주일 전시점의, 7일전 대비 전력 변화율

In [47]:
# train_ft['power_change_rate'] = (train_ft.groupby('building_num')['energy_consum'].shift(7*24) - train_ft.groupby('building_num')['energy_consum'].shift(7*2*24)) / train_ft.groupby('building_num')['energy_consum'].shift(7*2*24) #변화율 변경 기준을 7로도 바꿔볼 것
# train_ft['day_within_cycle'] = train_ft.index % (7*24)

# periodic_avg_power_change_rate = train_ft.groupby(['building_num','day_within_cycle' ])['power_change_rate'].mean().reset_index()
# periodic_avg_power_change_rate.rename(columns={'power_change_rate': 'periodic_avg_power_change_rate'}, inplace=True)

# train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num','day_within_cycle'], how='left')
# train_ft['power_change_rate'].fillna(train_ft['periodic_avg_power_change_rate'], inplace=True)

# cols = ['day_within_cycle','periodic_avg_power_change_rate']
# train_ft = train_ft.drop(columns = cols)


# last_rows = train_ft.groupby('building_num').tail(168)['power_change_rate'].reset_index().drop('index',axis=1) # train 데이터의 마지막 168행을 그대로 test셋에 적용
# test_ft = pd.concat([test_ft, last_rows], axis=1)

In [48]:
# #test
# # test_ft['power_change_rate'] = periodic_avg_power_change_rate['periodic_avg_power_change_rate']
# last_rows = train_ft.groupby('building_num').tail(7*2*24)['power_change_rate'].reset_index().drop('index',axis=1) # train 데이터의 마지막 168행을 그대로 test셋에 적용
# test_ft = pd.concat([test_ft, last_rows], axis=1)

In [49]:
# # import matplotlib.pyplot as plt
# cols = ['index']
# result_df = train_ft['power_change_rate'].reset_index().drop(columns=cols)
# result_df

In [50]:
# import matplotlib.pyplot as plt

# result_df *= 1000


# # 그래프 그리기
# plt.figure(figsize=(12, 6))
# plt.plot(result_df.values)
# plt.xlabel('Index')
# plt.ylabel('Scaled Periodic Avg Power Change Rate')
# # plt.title(f'Scaled Periodic Avg Power Change Rate for Building {building_num}')
# plt.legend(result_df.columns, title='Day within Cycle')
# plt.grid()
# plt.show()


- 6시간 전 대비 전력 벼노하율

In [51]:
# #train
# #test에는

# train_ft['power_change_rate_6h'] = (train_ft['energy_consum'] - train_ft.groupby('building_num')['energy_consum'].shift(6)) / train_ft.groupby('building_num')['energy_consum'].shift(6) #변화율 변경 기준을 7로도 바꿔볼 것
# train_ft['day_within_cycle'] = train_ft.index % (6)

# periodic_avg_power_change_rate = train_ft.groupby(['building_num','day_within_cycle' ])['power_change_rate_6h'].mean().reset_index()
# periodic_avg_power_change_rate.rename(columns={'power_change_rate_6h': 'periodic_avg_power_change_rate'}, inplace=True)

# train_ft = train_ft.merge(periodic_avg_power_change_rate, on=['building_num','day_within_cycle'], how='left')
# train_ft['power_change_rate_6h'].fillna(train_ft['periodic_avg_power_change_rate'], inplace=True)

# cols = ['day_within_cycle','periodic_avg_power_change_rate']
# train_ft = train_ft.drop(columns = cols)

# #test
# # test_ft['power_change_rate'] = periodic_avg_power_change_rate['periodic_avg_power_change_rate']
# last_rows = train_ft.groupby('building_num').tail(168)['power_change_rate_6h'].reset_index().drop('index',axis=1) # train 데이터의 마지막 168행을 그대로 test셋에 적용
# test_ft = pd.concat([test_ft, last_rows], axis=1)

In [52]:

train_ft = train_ft.interpolate()
test_ft = test_ft.interpolate()

train_ft.isnull().sum(), test_ft.isnull().sum()


(energy_consum                       0
 building_num                        0
 date_time                           0
 temp                                0
 precip                              0
 wind                                0
 hum                                 0
 building_type                       0
 time                                0
 day                                 0
 month                               0
 week                                0
 day_of_year                         0
 sin_time                            0
 cos_time                            0
 temp_RM                             0
 wind_RM                             0
 hum_RM                              0
 temp_EMA                            0
 wind_EMA                            0
 hum_EMA                             0
 THI                                 0
 feels_temp                          0
 CDH                                 0
 hour_mean                           0
 day_hour_mean           

## 피처추가

In [53]:
train_ft.columns

Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6'],
      dtype='object')

In [54]:
# train_ft['temp_product'] = train_ft['wind_RM'] *train_ft['temp_RM'] *train_ft['hum_RM'].std()
# test_ft['temp_product'] = test_ft['wind_RM'] *test_ft['temp_RM'] *test_ft['hum_RM'].std()


In [55]:
# train_df_1.columns

- 건물별 ft 생성

In [56]:
for i in range(1, 101):
    globals()[f'train_ft_{i}'] = train_ft[train_ft['building_num'] == i]

for i in range(1, 101):
    globals()[f'test_ft_{i}'] = test_ft[test_ft['building_num'] == i]

## 공휴일 반영

In [57]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_1['weekend'] = train_ft_1['day'].isin([6]) + 0
test_ft_1['weekend'] = test_ft_1['day'].isin([6]) + 0

mask = train_ft_1['day_of_year'] == 157
train_ft_1.loc[mask, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_2['weekend'] = train_ft_2['day'].isin([0]) + 0
test_ft_2['weekend'] = test_ft_2['day'].isin([0]) + 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_3['weekend'] = train_ft_3['day'].isin([0]) + 0
test_ft_3['weekend'] = test_ft_3['day'].isin([0]) + 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_5['weekend'] = train_ft_5['day'].isin([0, 1, 2, 3]) + 0
test_ft_5['weekend'] = test_ft_5['day'].isin([0, 1, 2, 3]) + 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_6['weekend'] = 0
test_ft_6['weekend'] = 0

mask_train = (train_ft_6['day_of_year'] == 163) | (train_ft_6['day_of_year'] == 177)| (train_ft_6['day_of_year'] == 191)| (train_ft_6['day_of_year'] == 205)| (train_ft_6['day_of_year'] == 226)
train_ft_6.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_6['day_of_year'] == 240
test_ft_6.loc[mask_test, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_7['weekend'] = train_ft_7['day'].isin([5, 6]) + 0
test_ft_7['weekend'] = test_ft_7['day'].isin([5, 6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_8['weekend'] = train_ft_8['day'].isin([6]) + 0
test_ft_8['weekend'] = test_ft_8['day'].isin([6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_9['weekend'] = 0
test_ft_9['weekend'] = 0

mask_train = (train_ft_9['day_of_year'] == 163) | (train_ft_9['day_of_year'] == 177)| (train_ft_9['day_of_year'] == 191)| (train_ft_9['day_of_year'] == 205)| (train_ft_9['day_of_year'] == 226)
train_ft_9.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_9['day_of_year'] == 240
test_ft_9.loc[mask_test, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_12['weekend'] = train_ft_12['day'].isin([6]) + 0
test_ft_12['weekend'] = test_ft_12['day'].isin([6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_14['weekend'] = train_ft_14['day'].isin([5,6]) + 0
test_ft_14['weekend'] = test_ft_14['day'].isin([5,6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_15['weekend'] = train_ft_15['day'].isin([5,6]) + 0
test_ft_15['weekend'] = test_ft_15['day'].isin([5,6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_16['weekend'] = train_ft_16['day'].isin([5, 6]) + 0
test_ft_16['weekend'] = test_ft_16['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_16['day_of_year'] == 157) | (train_ft_16['day_of_year'] == 227)
train_ft_16.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_17['weekend'] = train_ft_17['day'].isin([5, 6]) + 0
test_ft_17['weekend'] = test_ft_17['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_17['day_of_year'] == 157) | (train_ft_17['day_of_year'] == 227)
train_ft_17.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_18['weekend'] = train_ft_18['day'].isin([5, 6]) + 0
test_ft_18['weekend'] = test_ft_18['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_18['day_of_year'] == 157) | (train_ft_18['day_of_year'] == 227)
train_ft_18.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_19['weekend'] = train_ft_19['day'].isin([5, 6]) + 0
test_ft_19['weekend'] = test_ft_19['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_19['day_of_year'] == 157) | (train_ft_19['day_of_year'] == 227)
train_ft_19.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_20['weekend'] = train_ft_20['day'].isin([5, 6]) + 0

test_ft_20['weekend'] = test_ft_20['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_20['day_of_year'] == 157) | (train_ft_20['day_of_year'] == 227)
train_ft_20.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_21['weekend'] = train_ft_21['day'].isin([5, 6]) + 0
test_ft_21['weekend'] = test_ft_21['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_21['day_of_year'] == 157) | (train_ft_21['day_of_year'] == 227)
train_ft_21.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_22['weekend'] = train_ft_22['day'].isin([5, 6]) + 0
test_ft_22['weekend'] = test_ft_22['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_22['day_of_year'] == 157) | (train_ft_22['day_of_year'] == 227)
train_ft_22.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_23['weekend'] = train_ft_23['day'].isin([5, 6]) + 0
test_ft_23['weekend'] = test_ft_23['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_23['day_of_year'] == 157) | (train_ft_23['day_of_year'] == 227)
train_ft_23.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_24['weekend'] = train_ft_24['day'].isin([5, 6]) + 0
test_ft_24['weekend'] = test_ft_24['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_24['day_of_year'] == 157) | (train_ft_24['day_of_year'] == 227)
train_ft_24.loc[mask, 'weekend'] = 1

# 휴무일 지정(0: 영업일, 1: 휴무일)
train_ft_25['weekend'] = (train_ft_25['day'] == 0) + 0
test_ft_25['weekend'] = (test_ft_25['day'] == 0) + 0

# 8월 16일, 8월 17일 휴무일로 예상.
mask = (train_ft_25['day_of_year'] == 228) | (train_ft_25['day_of_year'] == 229)
train_ft_25.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_26['weekend'] = train_ft_26['day'].isin([5, 6]) + 0
test_ft_26['weekend'] = test_ft_26['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_26['day_of_year'] == 157) | (train_ft_26['day_of_year'] == 227)
train_ft_26.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_27['weekend'] = train_ft_27['day'].isin([5, 6]) + 0
test_ft_27['weekend'] = test_ft_27['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_27['day_of_year'] == 157) | (train_ft_27['day_of_year'] == 227)
train_ft_27.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_28['weekend'] = train_ft_28['day'].isin([5, 6]) + 0
test_ft_28['weekend'] = test_ft_28['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_28['day_of_year'] == 157) | (train_ft_28['day_of_year'] == 227)
train_ft_28.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_29['weekend'] = train_ft_29['day'].isin([5, 6]) + 0
test_ft_29['weekend'] = test_ft_29['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_29['day_of_year'] == 157) | (train_ft_29['day_of_year'] == 227)
train_ft_29.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_30['weekend'] = train_ft_30['day'].isin([5, 6]) + 0
test_ft_30['weekend'] = test_ft_30['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_30['day_of_year'] == 157) | (train_ft_30['day_of_year'] == 227)
train_ft_30.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_31['weekend'] = train_ft_31['day'].isin([5, 6]) + 0
test_ft_31['weekend'] = test_ft_31['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_31['day_of_year'] == 157) | (train_ft_31['day_of_year'] == 227)
train_ft_31.loc[mask, 'weekend'] = 1



<ipython-input-57-731d943b1092>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_ft_1['weekend'] = train_ft_1['day'].isin([6]) + 0
<ipython-input-57-731d943b1092>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_ft_1['weekend'] = test_ft_1['day'].isin([6]) + 0
<ipython-input-57-731d943b1092>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

In [58]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_37['closed'] = 0
mask = (train_ft_37['day_of_year'] == 171) | (train_ft_37['day_of_year'] == 192) | (train_ft_37['day_of_year'] == 220)
train_ft_37.loc[mask, 'closed'] = 1

test_ft_37['closed'] = 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_38['closed'] = 0
mask = (train_ft_38['day_of_year'] == 164) | (train_ft_38['day_of_year'] == 206) | (train_ft_38['day_of_year'] == 213)
train_ft_38.loc[mask, 'closed'] = 1

test_ft_38['closed'] = 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_39['closed'] = 0
mask = (train_ft_39['day_of_year'] == 199) | (train_ft_39['day_of_year'] == 220)
train_ft_39.loc[mask, 'closed'] = 1

test_ft_39['closed'] = 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_40['closed'] = 0
mask = (train_ft_40['day_of_year'] == 171) | (train_ft_40['day_of_year'] == 199) | (train_ft_40['day_of_year'] == 220)
train_ft_40.loc[mask, 'closed'] = 1

test_ft_40['closed'] = 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_41['closed'] = 0
mask = (train_ft_41['day_of_year'] == 178) | (train_ft_41['day_of_year'] == 206) | (train_ft_41['day_of_year'] == 220)
train_ft_41.loc[mask, 'closed'] = 1

test_ft_41['closed'] = 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_41['weekend'] = train_ft_41['day'].isin([5, 6]) + 0

test_ft_41['weekend'] = test_ft_41['day'].isin([5, 6]) + 0

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_42['closed'] = 0
mask = (train_ft_42['day_of_year'] == 164) | (train_ft_42['day_of_year'] == 192) | (train_ft_42['day_of_year'] == 234)
train_ft_42.loc[mask, 'closed'] = 1

test_ft_42['closed'] = 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_43['weekend'] = train_ft_43['day'].isin([5, 6]) + 0

test_ft_43['weekend'] = test_ft_43['day'].isin([5, 6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_44['weekend'] = train_ft_44['day'].isin([5, 6]) + 0

test_ft_44['weekend'] = test_ft_44['day'].isin([5, 6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_45['weekend'] = train_ft_45['day'].isin([5, 6]) + 0

test_ft_45['weekend'] = test_ft_45['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_45['day_of_year'] == 157) | (train_ft_45['day_of_year'] == 227)
train_ft_45.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_46['weekend'] = train_ft_46['day'].isin([5, 6]) + 0

test_ft_46['weekend'] = test_ft_46['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_46['day_of_year'] == 157) | (train_ft_46['day_of_year'] == 227)
train_ft_46.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_47['weekend'] = train_ft_47['day'].isin([5, 6]) + 0

test_ft_47['weekend'] = test_ft_47['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_47['day_of_year'] == 157) | (train_ft_47['day_of_year'] == 227)
train_ft_47.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_48['weekend'] = train_ft_48['day'].isin([5, 6]) + 0

test_ft_48['weekend'] = test_ft_48['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_48['day_of_year'] == 157) | (train_ft_48['day_of_year'] == 227)
train_ft_48.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_49['weekend'] = train_ft_49['day'].isin([5, 6]) + 0

test_ft_49['weekend'] = test_ft_49['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_49['day_of_year'] == 157) | (train_ft_49['day_of_year'] == 227)
train_ft_49.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_50['weekend'] = train_ft_50['day'].isin([5, 6]) + 0

test_ft_50['weekend'] = test_ft_50['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_50['day_of_year'] == 157) | (train_ft_50['day_of_year'] == 227)
train_ft_50.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_51['weekend'] = train_ft_51['day'].isin([5, 6]) + 0

test_ft_51['weekend'] = test_ft_51['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_51['day_of_year'] == 157) | (train_ft_51['day_of_year'] == 227)
train_ft_51.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_52['weekend'] = train_ft_52['day'].isin([5, 6]) + 0

test_ft_52['weekend'] = test_ft_52['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_52['day_of_year'] == 157) | (train_ft_52['day_of_year'] == 227)
train_ft_52.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_53['weekend'] = train_ft_53['day'].isin([5, 6]) + 0

test_ft_53['weekend'] = test_ft_53['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_53['day_of_year'] == 157) | (train_ft_53['day_of_year'] == 227)
train_ft_53.loc[mask, 'weekend'] = 1

# 휴무일 지정(0: 영업일, 1: 휴무일)
train_ft_54['weekend'] = (train_ft_54['day'] == 0) + 0

test_ft_54['weekend'] = (test_ft_54['day'] == 0) + 0

# 8월 16일, 8월 17일 휴무일로 예상.
mask = (train_ft_54['day_of_year'] == 228) | (train_ft_54['day_of_year'] == 229)
train_ft_54.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_55['weekend'] = train_ft_55['day'].isin([5, 6]) + 0

test_ft_55['weekend'] = test_ft_55['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_55['day_of_year'] == 157) | (train_ft_55['day_of_year'] == 227)
train_ft_55.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_56['weekend'] = train_ft_56['day'].isin([5, 6]) + 0

test_ft_56['weekend'] = test_ft_56['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_56['day_of_year'] == 157) | (train_ft_56['day_of_year'] == 227)
train_ft_56.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_57['weekend'] = train_ft_57['day'].isin([5, 6]) + 0

test_ft_57['weekend'] = test_ft_57['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_57['day_of_year'] == 157) | (train_ft_57['day_of_year'] == 227)
train_ft_57.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_58['weekend'] = train_ft_58['day'].isin([5, 6]) + 0

test_ft_58['weekend'] = test_ft_58['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_58['day_of_year'] == 157) | (train_ft_58['day_of_year'] == 227)
train_ft_58.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_59['weekend'] = train_ft_59['day'].isin([5, 6]) + 0

test_ft_59['weekend'] = test_ft_59['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_59['day_of_year'] == 157) | (train_ft_59['day_of_year'] == 227)
train_ft_59.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_60['weekend'] = train_ft_60['day'].isin([5, 6]) + 0

test_ft_60['weekend'] = test_ft_60['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_60['day_of_year'] == 157) | (train_ft_60['day_of_year'] == 227)
train_ft_60.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_61['weekend'] = train_ft_61['day'].isin([5, 6]) + 0

test_ft_61['weekend'] = test_ft_61['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_61['day_of_year'] == 157) | (train_ft_61['day_of_year'] == 227)
train_ft_61.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_62['weekend'] = train_ft_62['day'].isin([5, 6]) + 0

test_ft_62['weekend'] = test_ft_62['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_62['day_of_year'] == 157) | (train_ft_62['day_of_year'] == 227)
train_ft_62.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_63['weekend'] = train_ft_63['day'].isin([5, 6]) + 0

test_ft_63['weekend'] = test_ft_63['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_63['day_of_year'] == 157) | (train_ft_63['day_of_year'] == 227)
train_ft_63.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_64['weekend'] = train_ft_64['day'].isin([5, 6]) + 0

test_ft_64['weekend'] = test_ft_64['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_64['day_of_year'] == 157) | (train_ft_64['day_of_year'] == 227)
train_ft_64.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_65['weekend'] = train_ft_65['day'].isin([5, 6]) + 0

test_ft_65['weekend'] = test_ft_65['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_65['day_of_year'] == 157) | (train_ft_65['day_of_year'] == 227)
train_ft_65.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_66['weekend'] = train_ft_66['day'].isin([5, 6]) + 0

test_ft_66['weekend'] = test_ft_66['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_66['day_of_year'] == 157) | (train_ft_66['day_of_year'] == 227)
train_ft_66.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_67['weekend'] = train_ft_67['day'].isin([5, 6]) + 0

test_ft_67['weekend'] = test_ft_67['day'].isin([5, 6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_67['weekend'] = train_ft_67['day'].isin([5, 6]) + 0

test_ft_67['weekend'] = test_ft_67['day'].isin([5, 6]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_68['weekend'] = train_ft_68['day'].isin([5, 6]) + 0

test_ft_68['weekend'] = test_ft_68['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_68['day_of_year'] == 157) | (train_ft_68['day_of_year'] == 227)
train_ft_68.loc[mask, 'weekend'] = 1




<ipython-input-58-fd22beefbdde>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_ft_37['closed'] = 0
<ipython-input-58-fd22beefbdde>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_ft_37['closed'] = 0
<ipython-input-58-fd22beefbdde>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

In [59]:
# 주말 지정(0: 주중, 1: 주말)
train_ft_69['weekend'] = train_ft_69['day'].isin([5, 6]) + 0
test_ft_69['weekend'] = test_ft_69['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_69['day_of_year'] == 157) | (train_ft_69['day_of_year'] == 227)
train_ft_69.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_70['weekend'] = train_ft_70['day'].isin([5, 6]) + 0
test_ft_70['weekend'] = test_ft_70['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_70['day_of_year'] == 157) | (train_ft_70['day_of_year'] == 227)
train_ft_70.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_71['weekend'] = train_ft_71['day'].isin([5, 6]) + 0
test_ft_71['weekend'] = test_ft_71['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_71['day_of_year'] == 157) | (train_ft_71['day_of_year'] == 227)
train_ft_71.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_72['weekend'] = train_ft_72['day'].isin([5, 6]) + 0
test_ft_72['weekend'] = test_ft_72['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_72['day_of_year'] == 157) | (train_ft_72['day_of_year'] == 227)
train_ft_72.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_73['weekend'] = train_ft_73['day'].isin([5, 6]) + 0
test_ft_73['weekend'] = test_ft_73['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_73['day_of_year'] == 157) | (train_ft_73['day_of_year'] == 227)
train_ft_73.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_74['weekend'] = train_ft_74['day'].isin([5, 6]) + 0
test_ft_74['weekend'] = test_ft_74['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_74['day_of_year'] == 157) | (train_ft_74['day_of_year'] == 227)
train_ft_74.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_75['weekend'] = train_ft_75['day'].isin([5, 6, 0]) + 0
test_ft_75['weekend'] = test_ft_75['day'].isin([5, 6, 0]) + 0

# 주말 지정(0: 주중, 1: 주말)
train_ft_76['weekend'] = train_ft_76['day'].isin([5, 6]) + 0
test_ft_76['weekend'] = test_ft_76['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_76['day_of_year'] == 157) | (train_ft_76['day_of_year'] == 227)
train_ft_76.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_77['weekend'] = train_ft_77['day'].isin([5, 6]) + 0
test_ft_77['weekend'] = test_ft_77['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_77['day_of_year'] == 157) | (train_ft_77['day_of_year'] == 227)
train_ft_77.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_78['weekend'] = train_ft_78['day'].isin([5, 6]) + 0

test_ft_78['weekend'] = test_ft_78['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_78['day_of_year'] == 157) | (train_ft_78['day_of_year'] == 227)
train_ft_78.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_79['weekend'] = train_ft_79['day'].isin([5, 6]) + 0

test_ft_79['weekend'] = test_ft_79['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_79['day_of_year'] == 157) | (train_ft_79['day_of_year'] == 227)
train_ft_79.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_80['weekend'] = train_ft_80['day'].isin([5, 6]) + 0

test_ft_80['weekend'] = test_ft_80['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_80['day_of_year'] == 157) | (train_ft_80['day_of_year'] == 227)
train_ft_80.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_82['weekend'] = train_ft_82['day'].isin([5, 6]) + 0
test_ft_82['weekend'] = test_ft_82['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_82['day_of_year'] == 157) | (train_ft_82['day_of_year'] == 227)
train_ft_82.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_83['weekend'] = train_ft_83['day'].isin([5, 6]) + 0

test_ft_83['weekend'] = test_ft_83['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_83['day_of_year'] == 157) | (train_ft_83['day_of_year'] == 227)
train_ft_83.loc[mask, 'weekend'] = 1

# 주말 지정(0: 주중, 1: 주말)
train_ft_84['weekend'] = train_ft_84['day'].isin([5, 6]) + 0
test_ft_84['weekend'] = test_ft_84['day'].isin([5, 6]) + 0

# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_ft_84['day_of_year'] == 157) | (train_ft_84['day_of_year'] == 227)
train_ft_84.loc[mask, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_86['weekend'] = 0
test_ft_86['weekend'] = 0

mask_train = (train_ft_86['day_of_year'] == 161) | (train_ft_86['day_of_year'] == 177)| (train_ft_86['day_of_year'] == 191)| (train_ft_86['day_of_year'] == 205)| (train_ft_86['day_of_year'] == 222)
train_ft_86.loc[mask_train, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_87['weekend'] = 0
test_ft_87['weekend'] = 0

mask_train = (train_ft_87['day_of_year'] == 163) | (train_ft_87['day_of_year'] == 177)| (train_ft_87['day_of_year'] == 191)| (train_ft_87['day_of_year'] == 205)| (train_ft_87['day_of_year'] == 226)
train_ft_87.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_87['day_of_year'] == 240
test_ft_87.loc[mask_test, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_88['weekend'] = 0
test_ft_88['weekend'] = 0

mask_train = (train_ft_88['day_of_year'] == 163) | (train_ft_88['day_of_year'] == 177)| (train_ft_88['day_of_year'] == 191)| (train_ft_88['day_of_year'] == 205)| (train_ft_88['day_of_year'] == 226)
train_ft_88.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_88['day_of_year'] == 240
test_ft_88.loc[mask_test, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_89['weekend'] = 0
test_ft_89['weekend'] = 0

mask_train = (train_ft_89['day_of_year'] == 163) | (train_ft_89['day_of_year'] == 177)| (train_ft_89['day_of_year'] == 191)| (train_ft_89['day_of_year'] == 205)| (train_ft_89['day_of_year'] == 226)
train_ft_89.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_89['day_of_year'] == 240
test_ft_89.loc[mask_test, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_90['weekend'] = 0
test_ft_90['weekend'] = 0

mask_train = (train_ft_90['day_of_year'] == 163) | (train_ft_90['day_of_year'] == 177)| (train_ft_90['day_of_year'] == 191)| (train_ft_90['day_of_year'] == 205)| (train_ft_90['day_of_year'] == 226)
train_ft_90.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_90['day_of_year'] == 240
test_ft_90.loc[mask_test, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_91['weekend'] = 0
test_ft_91['weekend'] = 0

mask_train = (train_ft_91['day_of_year'] == 163) | (train_ft_91['day_of_year'] == 177)| (train_ft_91['day_of_year'] == 191)| (train_ft_91['day_of_year'] == 205)| (train_ft_91['day_of_year'] == 226)
train_ft_91.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_91['day_of_year'] == 240
test_ft_91.loc[mask_test, 'weekend'] = 1

# 휴무일 지정(1: 휴무일, 0: 영업일)
train_ft_92['weekend'] = 0
test_ft_92['weekend'] = 0

mask_train = (train_ft_92['day_of_year'] == 163) | (train_ft_92['day_of_year'] == 177)| (train_ft_92['day_of_year'] == 191)| (train_ft_92['day_of_year'] == 205)| (train_ft_92['day_of_year'] == 226)
train_ft_92.loc[mask_train, 'weekend'] = 1

mask_test = test_ft_92['day_of_year'] == 240
test_ft_92.loc[mask_test, 'weekend'] = 1




<ipython-input-59-3dcc50ac59b7>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_ft_69['weekend'] = train_ft_69['day'].isin([5, 6]) + 0
<ipython-input-59-3dcc50ac59b7>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_ft_69['weekend'] = test_ft_69['day'].isin([5, 6]) + 0
<ipython-input-59-3dcc50ac59b7>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https:/

- 공휴일 활용 피처 : weekend가 있는 건물들에 대해서 weekend의 왜도

## 개별 피처 추가 및 제거

- 이상 건물들의 train값 이상치 -> 전체 건물들의 이상치를 처리하는 방법

In [60]:
# for i in range(1,101):
#     second_largest = globals()[f'train_ft_{i}']['energy_consum'][globals()[f'train_ft_{i}']['energy_consum'] < globals()[f'train_ft_{i}']['energy_consum'].max()].nlargest(2).iloc[-1]
#     second_smallest = globals()[f'train_ft_{i}']['energy_consum'][globals()[f'train_ft_{i}']['energy_consum'] > globals()[f'train_ft_{i}']['energy_consum'].min()].nsmallest(2).iloc[-1]

#     # Replace maximum and minimum values with second largest and second smallest values
#     globals()[f'train_ft_{i}']['energy_consum'].replace(globals()[f'train_ft_{i}']['energy_consum'].max(), second_largest, inplace=True)
#     globals()[f'train_ft_{i}']['energy_consum'].replace(globals()[f'train_ft_{i}']['energy_consum'].min(), second_smallest, inplace=True)

In [61]:
# for i in range(1,101):
#     second_largest = globals()[f'test_ft_{i}']['energy_consum'][globals()[f'test_ft_{i}']['energy_consum'] < globals()[f'test_ft_{i}']['energy_consum'].max()].nlargest(2).iloc[-1]
#     second_smallest = globals()[f'test_ft_{i}']['energy_consum'][globals()[f'test_ft_{i}']['energy_consum'] > globals()[f'test_ft_{i}']['energy_consum'].min()].nsmallest(2).iloc[-1]

#     # Replace maximum and minimum values with second largest and second smallest values
#     globals()[f'test_ft_{i}']['energy_consum'].replace(globals()[f'test_ft_{i}']['energy_consum'].max(), second_largest, inplace=True)
#     globals()[f'test_ft_{i}']['energy_consum'].replace(globals()[f'test_ft_{i}']['energy_consum'].min(), second_smallest, inplace=True)

In [62]:
train_ft_1.columns


Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6',
       'weekend'],
      dtype='object')

- day of year 제거

In [63]:

# # Create a list to store train_ft and test_ft DataFrames
# train_ft_list = [globals()[f'train_ft_{i}'] for i in range(1, 101)]
# test_ft_list = [globals()[f'test_ft_{i}'] for i in range(1, 101)]

# # Iterate through each index (1 to 100)
# for i in range(1, 101):
#     train_df = train_ft_list[i-1]
#     test_df = test_ft_list[i-1]

#     # Check if 'weekend' column exists in the dataframe
#     if 'weekend' in train_df.columns:
#         # Filter buildings with weekends
#         buildings_with_weekends = train_df[train_df['weekend'] == 1]['building_num'].unique()

#         # Calculate skewness for each combination of building_num, day, and time on weekends
#         weekend_skewness_df = train_df[train_df['building_num'].isin(buildings_with_weekends)].groupby(['building_num', 'day', 'time'])['energy_consum'].apply(lambda x: np.nan if x.std() == 0 else x.skew()).reset_index()
#         weekend_skewness_df.rename(columns={'energy_consum': 'weekend_skewness'}, inplace=True)

#         # Merge weekend skewness values with train_df and test_df
#         train_df = pd.merge(train_df, weekend_skewness_df, on=['building_num', 'day', 'time'], how='left')
#         test_df = pd.merge(test_df, weekend_skewness_df, on=['building_num', 'day', 'time'], how='left')

#         # Fill missing values with 0 (or any other suitable value)
#         train_df['weekend_skewness'].fillna(0, inplace=True)
#         test_df['weekend_skewness'].fillna(0, inplace=True)

#         # Update the modified DataFrames in the list
#         train_ft_list[i-1] = train_df
#         test_ft_list[i-1] = test_df

# # Update the global DataFrames with the modified ones
# for i in range(1, 101):
#     globals()[f'train_ft_{i}'] = train_ft_list[i-1]
#     globals()[f'test_ft_{i}'] = test_ft_list[i-1]


- 공휴일의 왜도

In [64]:

# for i in range(1,101):
#     if 'weekend' in globals()[f'train_ft_{i}']:

#         buildings_with_weekends = globals()[f'train_ft_{i}'][globals()[f'train_ft_{i}']['weekend'] == 1]

#         # Calculate skewness for each combination of building_num and time on weekends
#         weekend_skewness_df = globals()[f'train_ft_{i}'][globals()[f'train_ft_{i}']['building_num'].isin(buildings_with_weekends)].groupby(['building_num','day','time'])['energy_consum'].apply(lambda x: np.nan if x.std() == 0 else x.skew()).reset_index()
#         weekend_skewness_df.rename(columns={'energy_consum': 'weekend_skewness'}, inplace=True)

#         # Merge weekend skewness values with train_ft
#         globals()[f'train_ft_{i}'] = pd.merge(globals()[f'train_ft_{i}'], weekend_skewness_df, on=['building_num','day','time'], how='left')
#         globals()[f'test_ft_{i}'] = pd.merge(globals()[f'test_ft_{i}'], weekend_skewness_df, on=['building_num','day','time'], how='left')
#         # Fill missing values with 0 (or any other suitable value)
#         globals()[f'train_ft_{i}']['weekend_skewness'].fillna(0, inplace=True)
#         globals()[f'test_ft_{i}']['weekend_skewness'].fillna(0, inplace=True)

In [65]:
# columns_to_drop = ['day_hour_mean']  # 삭제할 칼럼 이름들

# target_indices = [30, 51, 54, 56, 67, 71, 80, 82]  # 특정 i 값들


# for i in range(1, 101):
#     if i in target_indices:  # i 값이 특정 값인 경우에만 칼럼 삭제
#         train_subset = globals()[f'train_ft_{i}'].drop(columns=columns_to_drop)
#         test_subset = globals()[f'test_ft_{i}'].drop(columns=columns_to_drop)
#     else:
#         train_subset = globals()[f'train_ft_{i}']
#         test_subset = globals()[f'test_ft_{i}']

#     # 데이터 프레임 갱신
#     globals()[f'train_ft_{i}'] = train_subset
#     globals()[f'test_ft_{i}'] = test_subset

In [66]:
# columns_to_drop = ['precip']  # 삭제할 칼럼 이름들
# # target_indices = [1, 9, 15, 19, 25, 28, 32, 36, 41, 79, 81, 82, 91, 92, 99, 100]  # 특정 i 값들
# target_indices = [3,9,42, 54,72,82,91,92 ]  # 특정 i 값들


# for i in range(1, 101):
#     if i in target_indices:  # i 값이 특정 값인 경우에만 칼럼 삭제
#         train_subset = globals()[f'train_ft_{i}'].drop(columns=columns_to_drop)
#         test_subset = globals()[f'test_ft_{i}'].drop(columns=columns_to_drop)
#     else:
#         train_subset = globals()[f'train_ft_{i}']
#         test_subset = globals()[f'test_ft_{i}']

#     # 데이터 프레임 갱신
#     globals()[f'train_ft_{i}'] = train_subset
#     globals()[f'test_ft_{i}'] = test_subset

In [67]:
train_ft.columns

Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6'],
      dtype='object')

In [68]:
test_ft.columns

Index(['building_num', 'date_time', 'temp', 'precip', 'wind', 'hum',
       'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6'],
      dtype='object')

In [69]:
train_ft_1.columns

Index(['energy_consum', 'building_num', 'date_time', 'temp', 'precip', 'wind',
       'hum', 'building_type', 'time', 'day', 'month', 'week', 'day_of_year',
       'sin_time', 'cos_time', 'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA',
       'wind_EMA', 'hum_EMA', 'THI', 'feels_temp', 'CDH', 'hour_mean',
       'day_hour_mean', 'hour_std', 'heat_index', 'heat_wave', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6',
       'weekend'],
      dtype='object')

In [70]:


columns_to_drop = [ 'temp','wind', 'hum', # RM 때문에 제거할 칼럼
                   'heat_wave', 'heat_index',  # 필요 없어서 제거할 칼럼
                   'day_of_year','building_num','date_time','building_type','CDH','hour_std','precip','hour_mean'] #일조의 변화율?
                    # 'precip', 'hour_mean']  # 기본 제거할 칼럼

for i in range(1, 101):
    globals()[f'train_ft_{i}'] = globals()[f'train_ft_{i}'].drop(columns=columns_to_drop)
    globals()[f'test_ft_{i}'] = globals()[f'test_ft_{i}'].drop(columns=columns_to_drop)

- 함수

In [71]:
train_ft.iloc[:, 2:]

date_time  temp  precip  wind   hum building_type  time  day  month  \
0       20220602 00  18.1     0.0   0.4  67.0          건물기타     0    3      6   
1       20220602 01  17.6     0.0   0.8  69.0          건물기타     1    3      6   
2       20220602 02  17.2     0.0   0.7  71.0          건물기타     2    3      6   
3       20220602 03  17.2     0.0   2.2  75.0          건물기타     3    3      6   
4       20220602 04  17.2     0.0   2.0  81.0          건물기타     4    3      6   
...             ...   ...     ...   ...   ...           ...   ...  ...    ...   
201595  20220824 19  23.1     0.0   0.9  86.0        호텔및리조트    19    2      8   
201596  20220824 20  22.4     0.0   1.3  86.0        호텔및리조트    20    2      8   
201597  20220824 21  21.3     0.0   1.0  92.0        호텔및리조트    21    2      8   
201598  20220824 22  21.0     0.0   0.3  94.0        호텔및리조트    22    2      8   
201599  20220824 23  20.7     0.0   0.1  95.0        호텔및리조트    23    2      8   

        week  ...  feels_temp        CDH    hour_mean  day_hour_mean  \
0         22  ...   28.818026  -1.850000  1713.711429        1627.80   
1         22  ...   27.987268  -4.591667  1629.468571        1550.08   
2         22  ...   27.080175  -8.266667  1513.305714        1431.12   
3         22  ...   26.152269 -12.866667  1443.122857        1372.20   
4         22  ...   25.248724 -18.333333  1452.808571        1381.72   
...      ...  ...         ...        ...          ...            ...   
201595    34  ...   30.510262 -35.641667  1012.602857         976.06   
201596    34  ...   30.441848 -33.391667   930.205714         892.92   
201597    34  ...   30.233938 -31.266667   831.714286         786.62   
201598    34  ...   29.960151 -29.483333   724.480000         667.94   
201599    34  ...   29.663653 -28.083333   589.820000         566.94   

          hour_std  heat_index  heat_wave  temp_2  \
0       444.306331         0.0          0  327.61   
1       437.718795         0.0          0  309.76   
2       410.362488         0.0          0  295.84   
3       389.916262         0.0          0  295.84   
4       379.995696         0.0          0  295.84   
...            ...         ...        ...     ...   
201595  161.150392         0.0          0  533.61   
201596  137.040302         0.0          0  501.76   
201597  128.125250         0.0          0  453.69   
201598  112.413470         0.0          0  441.00   
201599   91.531822         0.0          0  428.49   

        periodic_avg_power_change_rate  periodic_avg_power_change_rate_6  
0                             0.069171                          0.021710  
1                             0.072765                          0.023154  
2                             0.071155                          0.025346  
3                             0.067707                          0.030905  
4                             0.063264                          0.033128  
...                                ...                               ...  
201595                        0.039282                          0.004240  
201596                        0.040570                          0.004927  
201597                        0.053521                          0.006987  
201598                        0.036985                          0.008615  
201599                        0.047592                          0.007734  

[201600 rows x 30 columns]

In [72]:
!pip install CatBoost

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.6/98.6 MB 8.9 MB/s eta 0:00:00


In [73]:
from catboost import CatBoostRegressor, Pool

# 데이터셋 만들기(마지막 7일간의 데이터를 검증데이터셋으로 사용)
def make_dataset(train_df, test_df):
    train_x = train_df.iloc[:, 2:]
    train_y = train_df['energy_consum']

    test_x = test_df.iloc[:, 1:]
    return train_x, train_y, test_x

def n_fold_train_test_split(train_x, train_y, n, test_size=168, week=11):
    x_valid = train_x[test_size * (week-n-1):test_size * (week-n)]
    y_valid = train_y[test_size * (week-n-1):test_size * (week-n)]
    x_train = train_x.drop(index=list(x_valid.index))
    y_train = train_y.drop(index=list(y_valid.index))
    return x_train, y_train, x_valid, y_valid

# CatBoostRegressor 모델
def catboost_predict(model, x_train, y_train, x_valid, y_valid, stopping=300):
    train_pool = Pool(data=x_train, label=y_train)
    valid_pool = Pool(data=x_valid, label=y_valid)

    model.fit(train_pool, eval_set=valid_pool, early_stopping_rounds=stopping, use_best_model=True, verbose=100)

    pred = model.predict(valid_pool)
    return pred

# test dataset 예측
def catboost_test_predict(model, train_x, train_y, test_x):
    train_pool = Pool(data=train_x, label=train_y)
    model.fit(train_pool)
    catboost_pred = model.predict(test_x)
    return catboost_pred

# CatBoost 모델 사용

# CatBoost 모델 사용
catboost_preds = np.array([])
fold = 4
smape_score_mean = []

def lgbm_evaluation(train_ft, test_ft): #catboost이나 이름만!!!!!!!

    global catboost_preds

    model = CatBoostRegressor(random_seed=SEED, loss_function='MAE')
    train_x, train_y, test_x = make_dataset(train_ft, test_ft)

    # 건물별 fold별 smape score
    smape_score = []
    for n in tqdm(range(fold)):
        x_train, y_train, x_valid, y_valid = n_fold_train_test_split(train_x, train_y, n=n)

        pred = catboost_predict(model, x_train, y_train, x_valid, y_valid, stopping=120)
        score = _smape(y_valid, pred)
        smape_score.append(score)

    smape_score_mean.append(np.mean(smape_score))

    catboost_pred = catboost_test_predict(model, train_x, train_y, test_x)
    catboost_preds = np.concatenate([catboost_preds, catboost_pred])

print(smape_score_mean)


[]


In [74]:
# from catboost import CatBoostRegressor, Pool

# # 데이터셋 만들기(마지막 7일간의 데이터를 검증데이터셋으로 사용)
# def make_dataset(train_df, test_df):
#     train_x = train_df.iloc[:, 2:]
#     train_y = train_df['energy_consum']

#     test_x = test_df.iloc[:, 1:]
#     return train_x, train_y, test_x

# def train_test_split(train_x, train_y, test_size=168):
#     y_train, y_valid, x_train, x_valid = temporal_train_test_split(y = train_y, X = train_x, test_size = test_size)
#     return x_train, y_train, x_valid, y_valid

In [75]:
# # n_fold로 데이터셋 나누기
# def n_fold_train_test_split(train_x, train_y, n, test_size=168, week=11):
#     x_valid = train_x[test_size * (week-n-1):test_size * (week-n)]
#     y_valid = train_y[test_size * (week-n-1):test_size * (week-n)]
#     x_train = train_x.drop(index = list(x_valid.index))
#     y_train = train_y.drop(index = list(y_valid.index))
#     return x_train, y_train, x_valid, y_valid

In [76]:

# # def lightgbm_smape(y_true, y_pred):
# #     smape_val = _smape(y_true, y_pred)
# #     return 'SMAPE', smape_val, False

# # LGBMRegressor 모델
# def lgbm_predict(model, x_train, y_train, x_valid, y_valid, stopping=300, eval_metric=lightgbm_smape):
#     model.fit(x_train, y_train, eval_set=[(x_train, y_train), (x_valid, y_valid)], callbacks = [early_stopping(stopping)], eval_metric=eval_metric)
#     pred = model.predict(x_valid)
#     pred = pd.Series(pred)
#     pred.index = np.arange(y_valid.index[0], y_valid.index[-1]+1)
#     plot_series(y_train, y_valid, pd.Series(pred), markers=[',' , ',', ','])
#     smape_score = _smape(y_valid, pred)
#     print(f"SMAPE_SCORE : {smape_score}")
#     return smape_score

# # test dataset 예측
# def lgbm_test_predict(model, train_x, train_y, test_x):
#     model.fit(train_x, train_y)
#     lgbm_pred = model.predict(test_x)
#     return lgbm_pred

In [77]:
# # LGBM 모델 사용

# # LGBM 모델 사용
# lgbm_preds = np.array([])
# fold = 4
# smape_score_mean = []

# def lgbm_evaluation(train_ft, test_ft) :
#     global lgbm_preds

#     model = LGBMRegressor(random_state=SEED, objective='regression')
#     train_x, train_y, test_x = make_dataset(train_ft, test_ft)
#     # 건물별 fold별 smape score
#     smape_score = []
#     for n in tqdm(range(fold)):
#         x_train, y_train, x_valid, y_valid = n_fold_train_test_split(train_x, train_y, n=n)

#         model.fit(x_train, y_train, eval_set=[(x_valid, y_valid)], callbacks = [early_stopping(120)], eval_metric=lightgbm_smape)

#         pred = model.predict(x_valid)
#         score = _smape(y_valid, pred)
#         smape_score.append(score)

#     smape_score_mean.append(np.mean(smape_score))

#     lgbm_pred = lgbm_test_predict(model, train_x, train_y, test_x)
#     lgbm_preds = np.concatenate([lgbm_preds, lgbm_pred])

# print(smape_score_mean)

## 1

In [78]:
lgbm_evaluation(train_ft_1, test_ft_1)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 922.7406461	test: 831.2675831	best: 831.2675831 (0)	total: 51.6ms	remaining: 51.6s
100:	learn: 162.6788622	test: 147.6123429	best: 147.4691897 (99)	total: 749ms	remaining: 6.67s
200:	learn: 123.1428125	test: 137.0529244	best: 137.0529244 (200)	total: 1.41s	remaining: 5.59s
300:	learn: 105.7151652	test: 139.1637674	best: 136.0892123 (268)	total: 2.15s	remaining: 5s
400:	learn: 93.4449649	test: 135.3959024	best: 134.9639542 (390)	total: 2.69s	remaining: 4.02s
500:	learn: 85.3339500	test: 132.8073771	best: 132.6121267 (487)	total: 2.97s	remaining: 2.96s
600:	learn: 79.6295557	test: 132.0301950	best: 131.8936574 (598)	total: 3.26s	remaining: 2.17s
700:	learn: 75.0602019	test: 131.2484877	best: 131.1448605 (694)	total: 3.52s	remaining: 1.5s
800:	learn: 70.9554135	test: 130.3545583	best: 130.1669732 (781)	total: 3.79s	remaining: 943ms
900:	learn: 67.9141990	test: 129.7422407	best: 129.7324167 (891)	total: 4.05s	remaining: 445ms
999:	learn: 65.2172740	test: 128.9017959	best: 128.729

In [79]:
train_ft_1.columns

Index(['energy_consum', 'time', 'day', 'month', 'week', 'sin_time', 'cos_time',
       'temp_RM', 'wind_RM', 'hum_RM', 'temp_EMA', 'wind_EMA', 'hum_EMA',
       'THI', 'feels_temp', 'day_hour_mean', 'temp_2',
       'periodic_avg_power_change_rate', 'periodic_avg_power_change_rate_6',
       'weekend'],
      dtype='object')

## 2

In [80]:
lgbm_evaluation(train_ft_2, test_ft_2)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 498.2864238	test: 578.8693572	best: 578.8693572 (0)	total: 7.13ms	remaining: 7.13s
100:	learn: 123.6718667	test: 168.7025196	best: 168.7025196 (100)	total: 705ms	remaining: 6.27s
200:	learn: 99.0501771	test: 155.1681758	best: 155.1681758 (200)	total: 1.39s	remaining: 5.54s
300:	learn: 86.9595458	test: 155.3706890	best: 154.6589219 (236)	total: 2.07s	remaining: 4.8s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 154.6589219
bestIteration = 236

Shrink model to first 237 iterations.
0:	learn: 490.8948360	test: 665.7140358	best: 665.7140358 (0)	total: 5.65ms	remaining: 5.64s
100:	learn: 125.3014210	test: 186.8302280	best: 186.8302280 (100)	total: 668ms	remaining: 5.95s
200:	learn: 101.2279683	test: 166.2969949	best: 166.0729012 (198)	total: 1.16s	remaining: 4.61s
300:	learn: 88.8828991	test: 159.9819264	best: 159.7467005 (297)	total: 1.43s	remaining: 3.31s
400:	learn: 79.3135144	test: 155.0387835	best: 155.0275197 (398)	total: 1.7s	remaining: 2.54s
500:	learn

## 3

In [81]:
lgbm_evaluation(train_ft_3, test_ft_3)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 463.4239961	test: 559.3625297	best: 559.3625297 (0)	total: 4.01ms	remaining: 4s
100:	learn: 150.9163102	test: 274.3885862	best: 273.6252970 (99)	total: 295ms	remaining: 2.63s
200:	learn: 120.2611063	test: 261.0816793	best: 260.5348882 (194)	total: 557ms	remaining: 2.22s
300:	learn: 105.3304559	test: 252.9143967	best: 252.9143967 (300)	total: 868ms	remaining: 2.02s
400:	learn: 95.0598327	test: 244.1297369	best: 243.9503868 (397)	total: 1.33s	remaining: 1.99s
500:	learn: 86.1197646	test: 241.9127421	best: 241.7469132 (494)	total: 1.88s	remaining: 1.87s
600:	learn: 79.7639432	test: 239.3676283	best: 238.8004275 (590)	total: 2.75s	remaining: 1.83s
700:	learn: 74.6479932	test: 237.1020255	best: 237.0200687 (693)	total: 3.41s	remaining: 1.46s
800:	learn: 71.0887133	test: 235.0036449	best: 234.9952326 (773)	total: 4.09s	remaining: 1.01s
900:	learn: 68.0625362	test: 233.8336461	best: 233.8294378 (891)	total: 4.77s	remaining: 525ms
999:	learn: 65.3935376	test: 234.2731178	best: 233.70

## 4

In [82]:
lgbm_evaluation(train_ft_4, test_ft_4)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 239.1766278	test: 282.6186090	best: 282.6186090 (0)	total: 12.7ms	remaining: 12.7s
100:	learn: 40.7685987	test: 74.0514413	best: 74.0514413 (100)	total: 1.58s	remaining: 14.1s
200:	learn: 31.8989939	test: 64.1901335	best: 64.1670323 (198)	total: 3.22s	remaining: 12.8s
300:	learn: 28.8620513	test: 63.1588772	best: 62.8299020 (261)	total: 4.66s	remaining: 10.8s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 62.829902
bestIteration = 261

Shrink model to first 262 iterations.
0:	learn: 237.7006919	test: 298.9890111	best: 298.9890111 (0)	total: 11.3ms	remaining: 11.3s
100:	learn: 41.5071019	test: 63.5271646	best: 63.5271646 (100)	total: 906ms	remaining: 8.06s
200:	learn: 31.9133590	test: 51.7991257	best: 51.7991257 (200)	total: 1.81s	remaining: 7.21s
300:	learn: 28.5072925	test: 50.8869383	best: 50.8320596 (258)	total: 2.74s	remaining: 6.37s
400:	learn: 26.0481205	test: 50.5749976	best: 50.5455939 (398)	total: 3.72s	remaining: 5.56s
500:	learn: 23.8171872	test

## 5

In [83]:
lgbm_evaluation(train_ft_5, test_ft_5)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1034.1623628	test: 1103.9480186	best: 1103.9480186 (0)	total: 10.4ms	remaining: 10.4s
100:	learn: 203.6526048	test: 232.7748920	best: 232.7748920 (100)	total: 700ms	remaining: 6.23s
200:	learn: 158.2953841	test: 199.5280261	best: 199.5280261 (200)	total: 1.25s	remaining: 4.97s
300:	learn: 134.4021836	test: 187.8417243	best: 187.8417243 (300)	total: 1.85s	remaining: 4.3s
400:	learn: 119.9996802	test: 181.5620927	best: 180.9787530 (396)	total: 2.51s	remaining: 3.75s
500:	learn: 109.6260838	test: 178.4075638	best: 178.4075638 (500)	total: 3.19s	remaining: 3.18s
600:	learn: 102.0970349	test: 177.3834604	best: 177.1874697 (581)	total: 3.86s	remaining: 2.56s
700:	learn: 95.8046558	test: 176.4221975	best: 176.3426373 (675)	total: 4.5s	remaining: 1.92s
800:	learn: 91.2050692	test: 175.5528414	best: 175.5528414 (800)	total: 4.8s	remaining: 1.19s
900:	learn: 86.3806509	test: 175.5651631	best: 175.1701959 (868)	total: 5.06s	remaining: 556ms
999:	learn: 83.4965886	test: 175.1267177	best:

## 6

In [84]:
lgbm_evaluation(train_ft_6, test_ft_6)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 665.3533509	test: 671.4248999	best: 671.4248999 (0)	total: 10.8ms	remaining: 10.8s
100:	learn: 75.2412940	test: 59.6883710	best: 59.6883710 (100)	total: 343ms	remaining: 3.05s
200:	learn: 52.9842616	test: 53.1010942	best: 52.4111209 (141)	total: 603ms	remaining: 2.4s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 52.41112091
bestIteration = 141

Shrink model to first 142 iterations.
0:	learn: 660.3425648	test: 733.6848427	best: 733.6848427 (0)	total: 2.42ms	remaining: 2.41s
100:	learn: 75.9434636	test: 102.9657507	best: 102.9657507 (100)	total: 257ms	remaining: 2.29s
200:	learn: 53.7488990	test: 66.6358150	best: 66.6358150 (200)	total: 543ms	remaining: 2.16s
300:	learn: 46.4347340	test: 60.7458176	best: 60.7458176 (300)	total: 810ms	remaining: 1.88s
400:	learn: 41.0134379	test: 58.5736225	best: 58.4600075 (398)	total: 1.07s	remaining: 1.6s
500:	learn: 37.3056027	test: 57.6202547	best: 57.6202547 (500)	total: 1.33s	remaining: 1.33s
600:	learn: 34.5547841	te

## 7

In [85]:
lgbm_evaluation(train_ft_7, test_ft_7)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 247.7126837	test: 257.3866134	best: 257.3866134 (0)	total: 4.03ms	remaining: 4.03s
100:	learn: 53.1264642	test: 55.6227673	best: 55.6227673 (100)	total: 569ms	remaining: 5.06s
200:	learn: 41.5514908	test: 52.8247620	best: 52.7357326 (171)	total: 1.22s	remaining: 4.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 52.73573256
bestIteration = 171

Shrink model to first 172 iterations.
0:	learn: 247.7395577	test: 257.4724982	best: 257.4724982 (0)	total: 6.55ms	remaining: 6.54s
100:	learn: 51.9359873	test: 60.9607083	best: 60.9607083 (100)	total: 690ms	remaining: 6.14s
200:	learn: 40.6535882	test: 61.2776542	best: 60.1003183 (117)	total: 1.34s	remaining: 5.33s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 60.10031827
bestIteration = 117

Shrink model to first 118 iterations.
0:	learn: 246.2019510	test: 274.4888402	best: 274.4888402 (0)	total: 3ms	remaining: 3s
100:	learn: 53.3905559	test: 67.6615628	best: 67.6252195 (99)	total: 556ms	rema

In [86]:
train_ft_7['energy_consum'].max

<bound method NDFrame._add_numeric_operations.<locals>.max of 12096    552.72
12097    548.64
12098    522.96
12099    518.88
12100    536.16
          ...  
14107    906.24
14108    831.60
14109    612.96
14110    462.96
14111    364.32
Name: energy_consum, Length: 2016, dtype: float64>

## 8

In [87]:
lgbm_evaluation(train_ft_8, test_ft_8)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 140.3869026	test: 141.6824219	best: 141.6824219 (0)	total: 2.95ms	remaining: 2.94s
100:	learn: 56.5729157	test: 70.1059111	best: 70.1059111 (100)	total: 279ms	remaining: 2.49s
200:	learn: 48.3296269	test: 69.5416657	best: 68.7328913 (133)	total: 565ms	remaining: 2.25s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 68.73289131
bestIteration = 133

Shrink model to first 134 iterations.
0:	learn: 139.7035219	test: 148.7010461	best: 148.7010461 (0)	total: 2.89ms	remaining: 2.89s
100:	learn: 56.6742452	test: 64.8188106	best: 64.8188106 (100)	total: 264ms	remaining: 2.35s
200:	learn: 48.2807362	test: 63.7708048	best: 63.2493278 (188)	total: 523ms	remaining: 2.08s
300:	learn: 43.2983220	test: 64.4976072	best: 63.2493278 (188)	total: 805ms	remaining: 1.87s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 63.24932783
bestIteration = 188

Shrink model to first 189 iterations.
0:	learn: 138.6109829	test: 159.1137193	best: 159.1137193 (0)	total: 2.69

## 9

In [88]:
lgbm_evaluation(train_ft_9, test_ft_9)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 749.1054747	test: 804.0608481	best: 804.0608481 (0)	total: 3.37ms	remaining: 3.37s
100:	learn: 81.5047351	test: 93.1004115	best: 93.1004115 (100)	total: 267ms	remaining: 2.37s
200:	learn: 53.8311594	test: 76.8896931	best: 76.4131944 (187)	total: 532ms	remaining: 2.12s
300:	learn: 45.2073725	test: 77.0045374	best: 76.4131944 (187)	total: 803ms	remaining: 1.86s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 76.41319445
bestIteration = 187

Shrink model to first 188 iterations.
0:	learn: 739.9263948	test: 907.5466199	best: 907.5466199 (0)	total: 2.88ms	remaining: 2.88s
100:	learn: 81.7843565	test: 158.6333833	best: 158.6333833 (100)	total: 268ms	remaining: 2.39s
200:	learn: 54.9374644	test: 106.0911950	best: 106.0911950 (200)	total: 539ms	remaining: 2.14s
300:	learn: 47.4375809	test: 96.2452748	best: 96.2452748 (300)	total: 791ms	remaining: 1.84s
400:	learn: 41.5396894	test: 91.2130109	best: 91.2130109 (400)	total: 1.05s	remaining: 1.56s
500:	learn: 37.786781

## 10

In [89]:
lgbm_evaluation(train_ft_10, test_ft_10)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 460.2373083	test: 336.9127861	best: 336.9127861 (0)	total: 8.79ms	remaining: 8.78s
100:	learn: 165.8533807	test: 286.5664119	best: 281.4907778 (33)	total: 678ms	remaining: 6.03s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 281.4907778
bestIteration = 33

Shrink model to first 34 iterations.
0:	learn: 461.3772311	test: 318.7815961	best: 318.7815961 (0)	total: 6.19ms	remaining: 6.19s
100:	learn: 173.3332920	test: 223.3722498	best: 219.2177960 (92)	total: 568ms	remaining: 5.05s
200:	learn: 136.0948348	test: 233.6009519	best: 219.2177960 (92)	total: 1.22s	remaining: 4.83s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 219.217796
bestIteration = 92

Shrink model to first 93 iterations.
0:	learn: 458.8898581	test: 345.0530676	best: 345.0530676 (0)	total: 3.58ms	remaining: 3.58s
100:	learn: 175.0611713	test: 259.4624284	best: 248.7621448 (55)	total: 603ms	remaining: 5.37s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 248

## 11

In [90]:
lgbm_evaluation(train_ft_11, test_ft_11)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 256.9675069	test: 264.0971889	best: 264.0971889 (0)	total: 3.17ms	remaining: 3.16s
100:	learn: 59.0315481	test: 70.2399015	best: 70.2399015 (100)	total: 282ms	remaining: 2.51s
200:	learn: 46.6499014	test: 67.0198162	best: 66.1256628 (172)	total: 567ms	remaining: 2.25s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 66.12566277
bestIteration = 172

Shrink model to first 173 iterations.
0:	learn: 255.7247777	test: 277.6787118	best: 277.6787118 (0)	total: 3.09ms	remaining: 3.08s
100:	learn: 58.0271514	test: 91.7391802	best: 91.7391802 (100)	total: 284ms	remaining: 2.53s
200:	learn: 45.6744092	test: 87.9907403	best: 87.9261252 (167)	total: 563ms	remaining: 2.24s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 87.92612515
bestIteration = 167

Shrink model to first 168 iterations.
0:	learn: 257.3205775	test: 259.9881611	best: 259.9881611 (0)	total: 2.83ms	remaining: 2.82s
100:	learn: 58.6347262	test: 80.7052471	best: 80.7052471 (100)	total: 267

## 12

In [91]:
lgbm_evaluation(train_ft_12, test_ft_12)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 230.6132242	test: 238.0116778	best: 238.0116778 (0)	total: 6.65ms	remaining: 6.64s
100:	learn: 60.8902728	test: 50.3528519	best: 50.3528519 (100)	total: 707ms	remaining: 6.29s
200:	learn: 47.3286894	test: 48.8439042	best: 48.0413598 (123)	total: 1.36s	remaining: 5.4s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 48.04135984
bestIteration = 123

Shrink model to first 124 iterations.
0:	learn: 229.2501077	test: 252.5384956	best: 252.5384956 (0)	total: 8.36ms	remaining: 8.35s
100:	learn: 57.0267952	test: 90.2948779	best: 89.9881409 (91)	total: 568ms	remaining: 5.05s
200:	learn: 43.8463387	test: 90.7187234	best: 89.2616227 (142)	total: 832ms	remaining: 3.31s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 89.2616227
bestIteration = 142

Shrink model to first 143 iterations.
0:	learn: 234.9670985	test: 186.2678210	best: 186.2678210 (0)	total: 3.49ms	remaining: 3.49s
100:	learn: 54.1081894	test: 124.4986486	best: 98.8313035 (31)	total: 273ms	

## 13

In [92]:
lgbm_evaluation(train_ft_13, test_ft_13)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 270.9455802	test: 249.4446108	best: 249.4446108 (0)	total: 8.26ms	remaining: 8.25s
100:	learn: 135.4568467	test: 159.6650679	best: 159.2860131 (99)	total: 275ms	remaining: 2.45s
200:	learn: 110.6947482	test: 158.6669232	best: 156.0699260 (137)	total: 541ms	remaining: 2.15s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 156.069926
bestIteration = 137

Shrink model to first 138 iterations.
0:	learn: 273.6813135	test: 221.3138364	best: 221.3138364 (0)	total: 13.4ms	remaining: 13.4s
100:	learn: 135.5365400	test: 171.4308006	best: 144.3282747 (38)	total: 283ms	remaining: 2.52s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 144.3282747
bestIteration = 38

Shrink model to first 39 iterations.
0:	learn: 268.2020862	test: 284.4961670	best: 284.4961670 (0)	total: 2.79ms	remaining: 2.78s
100:	learn: 133.1015859	test: 206.0460245	best: 204.3404557 (79)	total: 271ms	remaining: 2.41s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 

## 14

In [93]:
lgbm_evaluation(train_ft_14, test_ft_14)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 355.5170704	test: 408.1999732	best: 408.1999732 (0)	total: 8.31ms	remaining: 8.3s
100:	learn: 223.4371760	test: 303.9700162	best: 303.9700162 (100)	total: 280ms	remaining: 2.49s
200:	learn: 193.0750287	test: 308.5953451	best: 303.6261938 (150)	total: 549ms	remaining: 2.18s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 303.6261938
bestIteration = 150

Shrink model to first 151 iterations.
0:	learn: 362.8283641	test: 324.4583976	best: 324.4583976 (0)	total: 3.03ms	remaining: 3.03s
100:	learn: 226.7995413	test: 284.6406163	best: 281.8909535 (45)	total: 277ms	remaining: 2.47s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 281.8909535
bestIteration = 45

Shrink model to first 46 iterations.
0:	learn: 357.8264755	test: 382.1647243	best: 382.1647243 (0)	total: 2.85ms	remaining: 2.84s
100:	learn: 228.0265299	test: 280.3779066	best: 276.1843518 (82)	total: 280ms	remaining: 2.49s
200:	learn: 197.8013575	test: 294.3758780	best: 276.1843518 (82)	t

## 15

In [94]:
lgbm_evaluation(train_ft_15, test_ft_15)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 192.9792225	test: 171.6165800	best: 171.6165800 (0)	total: 3.02ms	remaining: 3.02s
100:	learn: 46.9086351	test: 96.7123235	best: 96.4820674 (97)	total: 285ms	remaining: 2.54s
200:	learn: 34.7876562	test: 94.5520995	best: 94.5281880 (195)	total: 556ms	remaining: 2.21s
300:	learn: 30.1453824	test: 93.8849643	best: 93.7819519 (284)	total: 859ms	remaining: 2s
400:	learn: 27.0979953	test: 93.5662076	best: 93.5658170 (399)	total: 1.14s	remaining: 1.7s
500:	learn: 24.7177304	test: 93.4450527	best: 93.3623737 (451)	total: 1.42s	remaining: 1.42s
600:	learn: 22.8964371	test: 93.0816857	best: 93.0299316 (585)	total: 1.71s	remaining: 1.13s
700:	learn: 21.5857257	test: 93.2294571	best: 93.0277093 (631)	total: 2s	remaining: 851ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 93.02770928
bestIteration = 631

Shrink model to first 632 iterations.
0:	learn: 190.4948624	test: 202.9562366	best: 202.9562366 (0)	total: 2.98ms	remaining: 2.97s
100:	learn: 49.2246808	test: 76.6

## 16

In [95]:
lgbm_evaluation(train_ft_16, test_ft_16)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1220.3041469	test: 1337.4480956	best: 1337.4480956 (0)	total: 5.64ms	remaining: 5.63s
100:	learn: 148.4661524	test: 164.8334717	best: 164.8334717 (100)	total: 287ms	remaining: 2.55s
200:	learn: 106.7122716	test: 131.4871025	best: 131.4871025 (200)	total: 545ms	remaining: 2.17s
300:	learn: 94.1702066	test: 130.3674351	best: 130.0456809 (241)	total: 805ms	remaining: 1.87s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 130.0456809
bestIteration = 241

Shrink model to first 242 iterations.
0:	learn: 1213.9972517	test: 1408.3542528	best: 1408.3542528 (0)	total: 2.68ms	remaining: 2.67s
100:	learn: 149.6764897	test: 200.3442128	best: 200.3442128 (100)	total: 281ms	remaining: 2.5s
200:	learn: 105.7398159	test: 132.3411319	best: 132.3411319 (200)	total: 540ms	remaining: 2.15s
300:	learn: 92.6640294	test: 121.0471325	best: 120.9846640 (299)	total: 800ms	remaining: 1.86s
400:	learn: 83.8801072	test: 117.0821999	best: 116.8910563 (396)	total: 1.06s	remaining: 1.58s
50

## 17

In [96]:
lgbm_evaluation(train_ft_17, test_ft_17)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 374.6966339	test: 325.1509795	best: 325.1509795 (0)	total: 15.2ms	remaining: 15.2s
100:	learn: 53.6871959	test: 70.6357599	best: 70.6016171 (98)	total: 278ms	remaining: 2.48s
200:	learn: 39.8089695	test: 71.3345378	best: 69.4286663 (128)	total: 547ms	remaining: 2.17s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 69.42866627
bestIteration = 128

Shrink model to first 129 iterations.
0:	learn: 368.5160659	test: 390.5892431	best: 390.5892431 (0)	total: 2.89ms	remaining: 2.88s
100:	learn: 53.2819465	test: 52.5521754	best: 52.5521754 (100)	total: 270ms	remaining: 2.4s
200:	learn: 40.0275174	test: 47.6010594	best: 47.6010594 (200)	total: 537ms	remaining: 2.13s
300:	learn: 34.8231632	test: 46.9540037	best: 46.9077640 (281)	total: 801ms	remaining: 1.86s
400:	learn: 31.0869677	test: 47.4448127	best: 46.6927992 (349)	total: 1.06s	remaining: 1.59s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 46.69279917
bestIteration = 349

Shrink model to firs

## 18

In [97]:
lgbm_evaluation(train_ft_18, test_ft_18)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 461.3623867	test: 431.8857546	best: 431.8857546 (0)	total: 5.32ms	remaining: 5.31s
100:	learn: 67.2564973	test: 97.8388208	best: 97.8388208 (100)	total: 284ms	remaining: 2.53s
200:	learn: 51.6158491	test: 101.3809373	best: 97.6729245 (101)	total: 566ms	remaining: 2.25s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 97.67292451
bestIteration = 101

Shrink model to first 102 iterations.
0:	learn: 451.9112022	test: 536.1149859	best: 536.1149859 (0)	total: 2.77ms	remaining: 2.77s
100:	learn: 64.3552096	test: 101.7666352	best: 101.7666352 (100)	total: 252ms	remaining: 2.24s
200:	learn: 49.1677231	test: 92.3001168	best: 92.3001168 (200)	total: 523ms	remaining: 2.08s
300:	learn: 44.2007588	test: 92.5576568	best: 92.2986846 (254)	total: 782ms	remaining: 1.82s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 92.29868462
bestIteration = 254

Shrink model to first 255 iterations.
0:	learn: 452.8249748	test: 529.2175289	best: 529.2175289 (0)	total: 2

## 19

In [98]:
lgbm_evaluation(train_ft_19, test_ft_19)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 571.1577294	test: 516.4615189	best: 516.4615189 (0)	total: 3.5ms	remaining: 3.5s
100:	learn: 63.2000501	test: 101.1719720	best: 99.6122328 (84)	total: 413ms	remaining: 3.67s
200:	learn: 43.0346954	test: 113.1607976	best: 99.6122328 (84)	total: 1.08s	remaining: 4.3s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 99.61223283
bestIteration = 84

Shrink model to first 85 iterations.
0:	learn: 562.7410797	test: 602.8335752	best: 602.8335752 (0)	total: 6.91ms	remaining: 6.91s
100:	learn: 64.3204597	test: 77.9072115	best: 77.9072115 (100)	total: 684ms	remaining: 6.09s
200:	learn: 43.0098472	test: 64.1122178	best: 64.1122178 (200)	total: 1.33s	remaining: 5.29s
300:	learn: 36.1402138	test: 65.5822972	best: 64.1122178 (200)	total: 1.86s	remaining: 4.31s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 64.11221781
bestIteration = 200

Shrink model to first 201 iterations.
0:	learn: 562.4496949	test: 617.9721053	best: 617.9721053 (0)	total: 6.34ms	re

## 20

In [99]:
lgbm_evaluation(train_ft_20, test_ft_20)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 752.7721929	test: 657.0204416	best: 657.0204416 (0)	total: 2.86ms	remaining: 2.86s
100:	learn: 86.7002420	test: 143.8351438	best: 143.8351438 (100)	total: 273ms	remaining: 2.43s
200:	learn: 61.7669894	test: 138.0770233	best: 137.6103563 (182)	total: 536ms	remaining: 2.13s
300:	learn: 55.2088430	test: 138.8826299	best: 137.6103563 (182)	total: 797ms	remaining: 1.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 137.6103563
bestIteration = 182

Shrink model to first 183 iterations.
0:	learn: 731.4600950	test: 872.0226567	best: 872.0226567 (0)	total: 2.75ms	remaining: 2.75s
100:	learn: 88.0034203	test: 123.3943081	best: 123.3943081 (100)	total: 279ms	remaining: 2.48s
200:	learn: 63.8880745	test: 98.5305219	best: 98.5305219 (200)	total: 548ms	remaining: 2.18s
300:	learn: 56.3696587	test: 97.9621031	best: 97.9066953 (219)	total: 815ms	remaining: 1.89s
400:	learn: 50.2620925	test: 98.9262447	best: 97.7929538 (310)	total: 1.07s	remaining: 1.6s
Stopped by overfit

## 21

In [100]:
lgbm_evaluation(train_ft_21, test_ft_21)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 592.1911725	test: 545.5638040	best: 545.5638040 (0)	total: 3.22ms	remaining: 3.22s
100:	learn: 96.9899208	test: 151.3939757	best: 151.3939757 (100)	total: 279ms	remaining: 2.49s
200:	learn: 78.1311468	test: 144.3402720	best: 144.2888340 (199)	total: 539ms	remaining: 2.14s
300:	learn: 69.1165974	test: 146.2036568	best: 142.7081636 (238)	total: 796ms	remaining: 1.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 142.7081636
bestIteration = 238

Shrink model to first 239 iterations.
0:	learn: 580.1020935	test: 688.5054922	best: 688.5054922 (0)	total: 2.74ms	remaining: 2.74s
100:	learn: 98.5983451	test: 117.4253654	best: 117.4253654 (100)	total: 278ms	remaining: 2.47s
200:	learn: 79.8262320	test: 98.4805767	best: 98.2840664 (193)	total: 552ms	remaining: 2.19s
300:	learn: 72.0269871	test: 98.2372783	best: 96.7669225 (231)	total: 843ms	remaining: 1.96s
400:	learn: 64.9755717	test: 97.9217284	best: 96.5886719 (322)	total: 1.12s	remaining: 1.68s
Stopped by overfi

## 22

In [101]:
lgbm_evaluation(train_ft_22, test_ft_22)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 261.2940868	test: 256.3834991	best: 256.3834991 (0)	total: 4.11ms	remaining: 4.11s
100:	learn: 43.9388286	test: 52.0552059	best: 52.0552059 (100)	total: 299ms	remaining: 2.66s
200:	learn: 35.1128897	test: 49.9529377	best: 49.9004358 (187)	total: 621ms	remaining: 2.47s
300:	learn: 31.9580908	test: 49.7627777	best: 49.6399314 (256)	total: 1.24s	remaining: 2.87s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 49.63993137
bestIteration = 256

Shrink model to first 257 iterations.
0:	learn: 260.7273371	test: 261.6512548	best: 261.6512548 (0)	total: 5.88ms	remaining: 5.87s
100:	learn: 45.0451261	test: 37.7903280	best: 37.7903280 (100)	total: 673ms	remaining: 5.99s
200:	learn: 36.0610070	test: 34.0042180	best: 33.5720352 (179)	total: 1.28s	remaining: 5.09s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 33.57203517
bestIteration = 179

Shrink model to first 180 iterations.
0:	learn: 258.8411779	test: 285.0548878	best: 285.0548878 (0)	total: 7.42

## 23

In [102]:
lgbm_evaluation(train_ft_23, test_ft_23)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 204.5005839	test: 181.1585155	best: 181.1585155 (0)	total: 3.94ms	remaining: 3.94s
100:	learn: 23.8228022	test: 41.1574105	best: 41.1574105 (100)	total: 278ms	remaining: 2.48s
200:	learn: 17.4906785	test: 39.9569585	best: 39.5375522 (120)	total: 540ms	remaining: 2.15s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 39.5375522
bestIteration = 120

Shrink model to first 121 iterations.
0:	learn: 199.1406379	test: 242.6829125	best: 242.6829125 (0)	total: 2.94ms	remaining: 2.94s
100:	learn: 24.8678489	test: 33.9459208	best: 33.9459208 (100)	total: 585ms	remaining: 5.21s
200:	learn: 18.4639521	test: 25.0405359	best: 25.0405359 (200)	total: 852ms	remaining: 3.39s
300:	learn: 16.3948781	test: 23.7155545	best: 23.6724686 (296)	total: 1.45s	remaining: 3.36s
400:	learn: 14.6948386	test: 23.1760827	best: 23.1675173 (399)	total: 1.71s	remaining: 2.56s
500:	learn: 13.6700453	test: 23.0096520	best: 22.9546670 (472)	total: 1.97s	remaining: 1.96s
Stopped by overfitting det

## 24

In [103]:
lgbm_evaluation(train_ft_24, test_ft_24)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 2292.5806346	test: 1997.8209894	best: 1997.8209894 (0)	total: 5.44ms	remaining: 5.44s
100:	learn: 267.5711611	test: 454.3172517	best: 454.3172517 (100)	total: 284ms	remaining: 2.53s
200:	learn: 172.2067317	test: 454.4973320	best: 451.4019676 (107)	total: 543ms	remaining: 2.16s
300:	learn: 145.4247371	test: 446.0993377	best: 445.5705600 (297)	total: 824ms	remaining: 1.91s
400:	learn: 126.4928970	test: 442.6309011	best: 442.1586341 (381)	total: 1.08s	remaining: 1.62s
500:	learn: 114.2141730	test: 440.3334614	best: 440.1820464 (497)	total: 1.37s	remaining: 1.36s
600:	learn: 104.3103161	test: 437.0036394	best: 436.7221570 (590)	total: 1.63s	remaining: 1.08s
700:	learn: 97.5977347	test: 437.4546255	best: 436.5144704 (647)	total: 1.9s	remaining: 808ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 436.5144704
bestIteration = 647

Shrink model to first 648 iterations.
0:	learn: 2250.2213131	test: 2458.5372182	best: 2458.5372182 (0)	total: 2.82ms	remaining: 2.82s


## 25

In [104]:
lgbm_evaluation(train_ft_25, test_ft_25)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1934.1182916	test: 1699.1085407	best: 1699.1085407 (0)	total: 11.2ms	remaining: 11.1s
100:	learn: 220.9546266	test: 466.3033580	best: 466.3033580 (100)	total: 610ms	remaining: 5.43s
200:	learn: 148.8061790	test: 457.1877769	best: 450.9837752 (143)	total: 1.16s	remaining: 4.62s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 450.9837752
bestIteration = 143

Shrink model to first 144 iterations.
0:	learn: 1908.2359865	test: 2030.6134637	best: 2030.6134637 (0)	total: 2.69ms	remaining: 2.69s
100:	learn: 237.0051539	test: 373.2760693	best: 373.2760693 (100)	total: 266ms	remaining: 2.37s
200:	learn: 161.9402077	test: 344.5300468	best: 336.5529284 (145)	total: 518ms	remaining: 2.06s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 336.5529284
bestIteration = 145

Shrink model to first 146 iterations.
0:	learn: 1903.4151196	test: 2090.8520544	best: 2090.8520544 (0)	total: 2.73ms	remaining: 2.73s
100:	learn: 243.6027177	test: 317.5868360	best: 317.

## 26

In [105]:
lgbm_evaluation(train_ft_26, test_ft_26)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 735.5643354	test: 658.9604249	best: 658.9604249 (0)	total: 2.69ms	remaining: 2.68s
100:	learn: 109.9167411	test: 147.2158436	best: 147.2158436 (100)	total: 271ms	remaining: 2.41s
200:	learn: 76.5108194	test: 135.6220128	best: 135.6220128 (200)	total: 539ms	remaining: 2.14s
300:	learn: 64.2775554	test: 133.0364813	best: 133.0364813 (300)	total: 815ms	remaining: 1.89s
400:	learn: 56.3933491	test: 131.6095312	best: 131.3994120 (384)	total: 1.09s	remaining: 1.63s
500:	learn: 50.5662183	test: 130.9170286	best: 130.5989375 (466)	total: 1.36s	remaining: 1.35s
600:	learn: 46.1005082	test: 130.2670222	best: 130.2473161 (597)	total: 1.64s	remaining: 1.09s
700:	learn: 42.8178862	test: 129.5417448	best: 129.4509308 (696)	total: 1.9s	remaining: 809ms
800:	learn: 40.1882056	test: 129.4861396	best: 129.4509308 (696)	total: 2.15s	remaining: 535ms
900:	learn: 37.9306006	test: 129.2896308	best: 129.2759188 (899)	total: 2.53s	remaining: 278ms
999:	learn: 36.1625246	test: 129.2434346	best: 129.1

## 27

In [106]:
lgbm_evaluation(train_ft_27, test_ft_27)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 2640.5479190	test: 2105.6365780	best: 2105.6365780 (0)	total: 4.43ms	remaining: 4.43s
100:	learn: 348.5643004	test: 614.1553985	best: 613.6645604 (98)	total: 283ms	remaining: 2.52s
200:	learn: 225.4762511	test: 624.5347228	best: 613.6483364 (104)	total: 549ms	remaining: 2.18s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 613.6483364
bestIteration = 104

Shrink model to first 105 iterations.
0:	learn: 2573.9652124	test: 3042.2208849	best: 3042.2208849 (0)	total: 2.68ms	remaining: 2.67s
100:	learn: 353.4475532	test: 681.3659824	best: 681.3659824 (100)	total: 269ms	remaining: 2.39s
200:	learn: 227.8665149	test: 458.0240734	best: 457.4793179 (199)	total: 534ms	remaining: 2.12s
300:	learn: 186.5123771	test: 419.2768139	best: 417.4330988 (297)	total: 796ms	remaining: 1.85s
400:	learn: 160.7132478	test: 409.2084642	best: 408.6669717 (385)	total: 1.06s	remaining: 1.58s
500:	learn: 145.2550207	test: 405.1306839	best: 403.0991438 (464)	total: 1.34s	remaining: 1.34s

## 28

In [107]:
lgbm_evaluation(train_ft_28, test_ft_28)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 467.8983659	test: 396.5358201	best: 396.5358201 (0)	total: 3.23ms	remaining: 3.23s
100:	learn: 83.8998876	test: 104.4423495	best: 104.4423495 (100)	total: 280ms	remaining: 2.49s
200:	learn: 60.5067149	test: 111.6273069	best: 104.1463692 (103)	total: 536ms	remaining: 2.13s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 104.1463692
bestIteration = 103

Shrink model to first 104 iterations.
0:	learn: 455.7543317	test: 537.3666652	best: 537.3666652 (0)	total: 2.94ms	remaining: 2.93s
100:	learn: 83.8984151	test: 162.8313972	best: 162.8313972 (100)	total: 265ms	remaining: 2.36s
200:	learn: 59.7043494	test: 140.5525080	best: 140.5525080 (200)	total: 540ms	remaining: 2.15s
300:	learn: 49.7669123	test: 141.8720298	best: 138.7718540 (231)	total: 799ms	remaining: 1.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 138.771854
bestIteration = 231

Shrink model to first 232 iterations.
0:	learn: 464.3141336	test: 467.8843940	best: 467.8843940 (0)	to

## 29

In [108]:
lgbm_evaluation(train_ft_29, test_ft_29)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 298.5293827	test: 247.2526576	best: 247.2526576 (0)	total: 8.58ms	remaining: 8.57s
100:	learn: 54.0590500	test: 79.9831913	best: 79.5937440 (92)	total: 573ms	remaining: 5.1s
200:	learn: 39.7557356	test: 77.8353331	best: 77.7355652 (195)	total: 835ms	remaining: 3.32s
300:	learn: 34.4577295	test: 76.2379631	best: 76.2379631 (300)	total: 1.1s	remaining: 2.55s
400:	learn: 30.7348377	test: 75.1500552	best: 75.1289997 (399)	total: 1.35s	remaining: 2.01s
500:	learn: 27.7956728	test: 75.3835807	best: 74.9467963 (447)	total: 1.62s	remaining: 1.62s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 74.94679628
bestIteration = 447

Shrink model to first 448 iterations.
0:	learn: 286.6436752	test: 377.3136368	best: 377.3136368 (0)	total: 5.1ms	remaining: 5.09s
100:	learn: 53.7887493	test: 104.3542803	best: 104.3542803 (100)	total: 271ms	remaining: 2.41s
200:	learn: 39.5354130	test: 72.8611070	best: 72.8611070 (200)	total: 533ms	remaining: 2.12s
300:	learn: 34.0635390	test

## 30

In [109]:
lgbm_evaluation(train_ft_30, test_ft_30)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 177.6191355	test: 134.4022806	best: 134.4022806 (0)	total: 3.27ms	remaining: 3.27s
100:	learn: 53.7238833	test: 87.1015796	best: 79.3860933 (46)	total: 508ms	remaining: 4.52s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 79.38609327
bestIteration = 46

Shrink model to first 47 iterations.
0:	learn: 170.5933826	test: 212.8322844	best: 212.8322844 (0)	total: 5.93ms	remaining: 5.92s
100:	learn: 55.1483342	test: 75.8276094	best: 75.8276094 (100)	total: 687ms	remaining: 6.12s
200:	learn: 43.0404243	test: 65.6582363	best: 65.6582363 (200)	total: 1.27s	remaining: 5.05s
300:	learn: 36.7014968	test: 62.4961904	best: 62.4961904 (300)	total: 1.92s	remaining: 4.47s
400:	learn: 32.3627679	test: 61.9942664	best: 61.4997521 (367)	total: 2.54s	remaining: 3.79s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 61.49975213
bestIteration = 367

Shrink model to first 368 iterations.
0:	learn: 174.2073680	test: 171.9324652	best: 171.9324652 (0)	total: 3.28ms	

## 31

In [110]:
lgbm_evaluation(train_ft_31, test_ft_31)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 315.0810117	test: 275.5430550	best: 275.5430550 (0)	total: 3.62ms	remaining: 3.62s
100:	learn: 56.3960741	test: 75.4494047	best: 75.3687695 (97)	total: 289ms	remaining: 2.57s
200:	learn: 41.2800477	test: 73.2160499	best: 73.0063905 (185)	total: 546ms	remaining: 2.17s
300:	learn: 35.1196073	test: 72.4335766	best: 72.2040227 (263)	total: 804ms	remaining: 1.86s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 72.20402272
bestIteration = 263

Shrink model to first 264 iterations.
0:	learn: 305.1597126	test: 393.4990723	best: 393.4990723 (0)	total: 2.86ms	remaining: 2.86s
100:	learn: 54.6837161	test: 135.3651637	best: 135.3651637 (100)	total: 269ms	remaining: 2.4s
200:	learn: 39.5143462	test: 119.3584671	best: 119.3584671 (200)	total: 558ms	remaining: 2.22s
300:	learn: 34.3031267	test: 117.7413664	best: 117.5974800 (295)	total: 818ms	remaining: 1.9s
400:	learn: 30.7406589	test: 117.5279090	best: 117.3480934 (344)	total: 1.08s	remaining: 1.61s
500:	learn: 27.92221

## 32

In [111]:
lgbm_evaluation(train_ft_32, test_ft_32)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 174.4010860	test: 73.4530727	best: 73.4530727 (0)	total: 12.3ms	remaining: 12.3s
100:	learn: 41.5889982	test: 43.0694444	best: 43.0694444 (100)	total: 263ms	remaining: 2.34s
200:	learn: 30.0473421	test: 38.3722973	best: 38.2686858 (198)	total: 513ms	remaining: 2.04s
300:	learn: 25.2029445	test: 36.3249049	best: 36.3249049 (300)	total: 794ms	remaining: 1.84s
400:	learn: 22.0508769	test: 35.0938327	best: 35.0938327 (400)	total: 1.05s	remaining: 1.57s
500:	learn: 19.9866669	test: 34.0157694	best: 33.9942886 (489)	total: 1.31s	remaining: 1.3s
600:	learn: 18.4049707	test: 33.6893831	best: 33.6865682 (599)	total: 1.57s	remaining: 1.04s
700:	learn: 17.0646795	test: 33.1787037	best: 33.1723746 (696)	total: 1.85s	remaining: 791ms
800:	learn: 15.8789955	test: 33.0577541	best: 33.0077400 (781)	total: 2.12s	remaining: 528ms
900:	learn: 14.8949301	test: 32.8692060	best: 32.8651523 (898)	total: 2.38s	remaining: 262ms
999:	learn: 14.1218935	test: 32.6165426	best: 32.6165426 (999)	total: 2.6

## 33

In [112]:
lgbm_evaluation(train_ft_33, test_ft_33)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 151.6616868	test: 84.1559087	best: 84.1559087 (0)	total: 3.25ms	remaining: 3.25s
100:	learn: 32.6614177	test: 28.5510440	best: 26.9841177 (59)	total: 281ms	remaining: 2.5s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 26.98411766
bestIteration = 59

Shrink model to first 60 iterations.
0:	learn: 143.8222788	test: 178.8479249	best: 178.8479249 (0)	total: 2.53ms	remaining: 2.52s
100:	learn: 32.9440992	test: 56.7011107	best: 56.7011107 (100)	total: 259ms	remaining: 2.31s
200:	learn: 23.7623483	test: 40.2432236	best: 40.2432236 (200)	total: 528ms	remaining: 2.1s
300:	learn: 19.7186765	test: 37.4542713	best: 37.3891890 (297)	total: 790ms	remaining: 1.83s
400:	learn: 16.8453995	test: 36.4912784	best: 36.4666510 (396)	total: 1.08s	remaining: 1.62s
500:	learn: 15.0170738	test: 35.9092605	best: 35.8572557 (499)	total: 1.34s	remaining: 1.34s
600:	learn: 13.6587989	test: 35.3515943	best: 35.3469353 (598)	total: 1.6s	remaining: 1.06s
700:	learn: 12.7008634	test: 35.2

## 34

In [113]:
lgbm_evaluation(train_ft_34, test_ft_34)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 106.8402722	test: 63.8459149	best: 63.8459149 (0)	total: 4.98ms	remaining: 4.98s
100:	learn: 22.8924262	test: 28.5230845	best: 28.5230845 (100)	total: 634ms	remaining: 5.64s
200:	learn: 17.3651858	test: 27.4482682	best: 27.4369194 (199)	total: 1.25s	remaining: 4.96s
300:	learn: 14.9407654	test: 27.1019602	best: 27.0980695 (298)	total: 1.81s	remaining: 4.21s
400:	learn: 13.1291007	test: 26.5651670	best: 26.5642267 (399)	total: 2.08s	remaining: 3.1s
500:	learn: 11.8336254	test: 26.1962712	best: 26.1962712 (500)	total: 2.34s	remaining: 2.33s
600:	learn: 10.8773650	test: 25.8140886	best: 25.8140886 (600)	total: 2.61s	remaining: 1.73s
700:	learn: 10.0968290	test: 25.7625911	best: 25.7341421 (622)	total: 2.9s	remaining: 1.24s
800:	learn: 9.4702837	test: 25.5364953	best: 25.5364953 (800)	total: 3.18s	remaining: 790ms
900:	learn: 8.9173743	test: 25.4281121	best: 25.4132382 (875)	total: 3.45s	remaining: 379ms
999:	learn: 8.4990437	test: 25.3525817	best: 25.3454492 (934)	total: 3.71s	r

## 35

In [114]:
lgbm_evaluation(train_ft_35, test_ft_35)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 37.9231654	test: 20.9527858	best: 20.9527858 (0)	total: 2.77ms	remaining: 2.76s
100:	learn: 9.3924464	test: 10.2822135	best: 9.1353461 (51)	total: 269ms	remaining: 2.4s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 9.135346072
bestIteration = 51

Shrink model to first 52 iterations.
0:	learn: 35.8572136	test: 45.5291744	best: 45.5291744 (0)	total: 2.65ms	remaining: 2.65s
100:	learn: 9.4401578	test: 17.5525148	best: 17.5525148 (100)	total: 288ms	remaining: 2.57s
200:	learn: 7.0929322	test: 13.8432217	best: 13.8432217 (200)	total: 555ms	remaining: 2.21s
300:	learn: 5.9960723	test: 12.9010672	best: 12.9010672 (300)	total: 823ms	remaining: 1.91s
400:	learn: 5.3882272	test: 12.7631826	best: 12.7381805 (379)	total: 1.36s	remaining: 2.03s
500:	learn: 4.9275031	test: 12.5756029	best: 12.5571712 (496)	total: 2s	remaining: 1.99s
600:	learn: 4.6103313	test: 12.4371315	best: 12.4286060 (594)	total: 2.65s	remaining: 1.76s
700:	learn: 4.3225121	test: 12.4301391	best: 1

## 36

In [115]:
lgbm_evaluation(train_ft_36, test_ft_36)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 44.7010525	test: 36.7304581	best: 36.7304581 (0)	total: 3.56ms	remaining: 3.56s
100:	learn: 14.5528239	test: 14.8121281	best: 14.6770150 (78)	total: 274ms	remaining: 2.44s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 14.67701501
bestIteration = 78

Shrink model to first 79 iterations.
0:	learn: 43.5544587	test: 49.7731823	best: 49.7731823 (0)	total: 2.85ms	remaining: 2.85s
100:	learn: 14.2904616	test: 36.4641335	best: 36.4641335 (100)	total: 281ms	remaining: 2.5s
200:	learn: 10.6310770	test: 32.9099201	best: 32.9099201 (200)	total: 568ms	remaining: 2.26s
300:	learn: 8.9981470	test: 31.5127959	best: 31.5127959 (300)	total: 823ms	remaining: 1.91s
400:	learn: 7.9283901	test: 30.5176759	best: 30.5176759 (400)	total: 1.19s	remaining: 1.78s
500:	learn: 7.1823382	test: 29.7689524	best: 29.7509864 (497)	total: 1.85s	remaining: 1.84s
600:	learn: 6.6020667	test: 29.4547477	best: 29.4444569 (598)	total: 2.52s	remaining: 1.67s
700:	learn: 6.1531681	test: 29.0371438	

## 37

In [116]:
lgbm_evaluation(train_ft_37, test_ft_37)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1814.8785096	test: 1856.8761862	best: 1856.8761862 (0)	total: 2.86ms	remaining: 2.86s
100:	learn: 160.6565365	test: 172.7253207	best: 172.7253207 (100)	total: 272ms	remaining: 2.42s
200:	learn: 96.3942756	test: 142.5661098	best: 142.5661098 (200)	total: 537ms	remaining: 2.13s
300:	learn: 80.0747504	test: 135.8725684	best: 135.5581570 (298)	total: 820ms	remaining: 1.9s
400:	learn: 70.0214070	test: 133.4373771	best: 133.4158744 (393)	total: 1.11s	remaining: 1.67s
500:	learn: 63.6608068	test: 130.0654014	best: 130.0654014 (500)	total: 1.38s	remaining: 1.37s
600:	learn: 58.8231642	test: 129.2970669	best: 129.2932864 (587)	total: 1.66s	remaining: 1.1s
700:	learn: 55.2933739	test: 129.1277321	best: 129.0648513 (664)	total: 1.93s	remaining: 821ms
800:	learn: 52.4740729	test: 128.9386064	best: 128.3949039 (794)	total: 2.2s	remaining: 548ms
900:	learn: 49.8037739	test: 128.0549861	best: 128.0549861 (900)	total: 2.48s	remaining: 273ms
999:	learn: 47.8982773	test: 127.5503864	best: 127.

## 38

In [117]:
lgbm_evaluation(train_ft_38, test_ft_38)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1119.1144854	test: 1158.2290571	best: 1158.2290571 (0)	total: 5.17ms	remaining: 5.16s
100:	learn: 89.1929676	test: 69.5440446	best: 69.5440446 (100)	total: 580ms	remaining: 5.16s
200:	learn: 48.4642379	test: 59.8325261	best: 59.8325261 (200)	total: 1.26s	remaining: 5.02s
300:	learn: 40.9109836	test: 56.3230625	best: 56.3230625 (300)	total: 1.92s	remaining: 4.46s
400:	learn: 35.8974011	test: 54.1810799	best: 54.1810799 (400)	total: 2.59s	remaining: 3.87s
500:	learn: 32.4826946	test: 52.9101189	best: 52.9076599 (499)	total: 3.25s	remaining: 3.24s
600:	learn: 30.2527637	test: 52.4348581	best: 52.3565649 (590)	total: 3.91s	remaining: 2.59s
700:	learn: 28.4930801	test: 52.2961024	best: 52.2267776 (676)	total: 4.54s	remaining: 1.94s
800:	learn: 26.8646029	test: 51.8875108	best: 51.6351216 (773)	total: 4.81s	remaining: 1.2s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 51.63512156
bestIteration = 773

Shrink model to first 774 iterations.
0:	learn: 1115.1231417	

## 39

In [118]:
lgbm_evaluation(train_ft_39, test_ft_39)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1257.7613508	test: 1268.7679959	best: 1268.7679959 (0)	total: 3.29ms	remaining: 3.28s
100:	learn: 96.6765427	test: 72.5892930	best: 72.5892930 (100)	total: 281ms	remaining: 2.5s
200:	learn: 47.0765376	test: 43.8014263	best: 43.7393996 (199)	total: 546ms	remaining: 2.17s
300:	learn: 36.7014723	test: 42.7181222	best: 42.7181222 (300)	total: 806ms	remaining: 1.87s
400:	learn: 31.8154038	test: 42.0073433	best: 42.0045177 (399)	total: 1.07s	remaining: 1.6s
500:	learn: 28.7569957	test: 41.5452095	best: 41.4259919 (471)	total: 1.33s	remaining: 1.33s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 41.42599187
bestIteration = 471

Shrink model to first 472 iterations.
0:	learn: 1255.0352767	test: 1298.5791450	best: 1298.5791450 (0)	total: 2.77ms	remaining: 2.77s
100:	learn: 89.8001851	test: 263.4582238	best: 263.4582238 (100)	total: 258ms	remaining: 2.29s
200:	learn: 44.9165751	test: 212.8528049	best: 212.8528049 (200)	total: 524ms	remaining: 2.08s
300:	learn: 35.88

## 40

In [119]:
lgbm_evaluation(train_ft_40, test_ft_40)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1243.6740739	test: 1445.3474518	best: 1445.3474518 (0)	total: 8.7ms	remaining: 8.69s
100:	learn: 134.8430772	test: 219.1190348	best: 219.1190348 (100)	total: 284ms	remaining: 2.52s
200:	learn: 88.0323215	test: 167.4364051	best: 167.1365481 (191)	total: 543ms	remaining: 2.16s
300:	learn: 76.5174311	test: 166.7321447	best: 166.3015134 (271)	total: 799ms	remaining: 1.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 166.3015134
bestIteration = 271

Shrink model to first 272 iterations.
0:	learn: 1255.0168961	test: 1315.0286286	best: 1315.0286286 (0)	total: 2.85ms	remaining: 2.85s
100:	learn: 136.0872427	test: 299.9039204	best: 299.9039204 (100)	total: 276ms	remaining: 2.46s
200:	learn: 89.5191089	test: 246.2605323	best: 246.2605323 (200)	total: 526ms	remaining: 2.09s
300:	learn: 78.4996202	test: 232.2909114	best: 232.2909114 (300)	total: 772ms	remaining: 1.79s
400:	learn: 70.8715038	test: 228.4611334	best: 228.3186966 (399)	total: 1.04s	remaining: 1.55s
500:

## 41

In [120]:
lgbm_evaluation(train_ft_41, test_ft_41)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1649.1656272	test: 1722.0529259	best: 1722.0529259 (0)	total: 10.5ms	remaining: 10.5s
100:	learn: 171.8101129	test: 226.9905847	best: 226.9905847 (100)	total: 262ms	remaining: 2.33s
200:	learn: 106.0819132	test: 186.6038617	best: 186.6038617 (200)	total: 529ms	remaining: 2.1s
300:	learn: 88.1587617	test: 182.2309101	best: 182.2309101 (300)	total: 780ms	remaining: 1.81s
400:	learn: 77.6404985	test: 180.3247152	best: 180.0617191 (359)	total: 1.04s	remaining: 1.55s
500:	learn: 70.5011574	test: 177.9061453	best: 177.8579962 (499)	total: 1.3s	remaining: 1.29s
600:	learn: 65.9646939	test: 177.4146569	best: 177.3862515 (595)	total: 1.55s	remaining: 1.03s
700:	learn: 62.0178623	test: 175.8423253	best: 175.8130717 (697)	total: 1.8s	remaining: 768ms
800:	learn: 58.6687928	test: 175.5937289	best: 175.5699608 (788)	total: 2.06s	remaining: 511ms
900:	learn: 55.2351706	test: 175.1120417	best: 175.1120417 (900)	total: 2.32s	remaining: 255ms
999:	learn: 52.9428592	test: 174.8192594	best: 174

## 42

In [121]:
lgbm_evaluation(train_ft_42, test_ft_42)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1114.1731213	test: 1203.3423417	best: 1203.3423417 (0)	total: 13.7ms	remaining: 13.7s
100:	learn: 83.6215516	test: 87.9649624	best: 87.9649624 (100)	total: 636ms	remaining: 5.66s
200:	learn: 44.7489941	test: 42.8498630	best: 42.7685695 (197)	total: 1.12s	remaining: 4.47s
300:	learn: 37.0430719	test: 39.4015434	best: 39.4015434 (300)	total: 1.39s	remaining: 3.24s
400:	learn: 32.4037734	test: 38.5152597	best: 38.5152597 (400)	total: 1.66s	remaining: 2.48s
500:	learn: 29.3625769	test: 37.8250759	best: 37.8250759 (500)	total: 1.92s	remaining: 1.91s
600:	learn: 27.2540430	test: 37.7409255	best: 37.7304884 (579)	total: 2.21s	remaining: 1.47s
700:	learn: 25.4275822	test: 37.4262784	best: 37.4262784 (700)	total: 2.48s	remaining: 1.06s
800:	learn: 23.8491392	test: 37.4696415	best: 37.2923212 (716)	total: 2.74s	remaining: 680ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 37.29232119
bestIteration = 716

Shrink model to first 717 iterations.
0:	learn: 1111.7106657

## 43

In [122]:
lgbm_evaluation(train_ft_43, test_ft_43)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1347.7367001	test: 1453.1234084	best: 1453.1234084 (0)	total: 5.94ms	remaining: 5.93s
100:	learn: 106.3397428	test: 109.9113978	best: 109.9113978 (100)	total: 264ms	remaining: 2.35s
200:	learn: 59.3089173	test: 85.1602841	best: 85.1602841 (200)	total: 521ms	remaining: 2.07s
300:	learn: 49.5845868	test: 81.0119308	best: 81.0086055 (299)	total: 772ms	remaining: 1.79s
400:	learn: 43.9087086	test: 77.5413242	best: 77.5277065 (399)	total: 1.04s	remaining: 1.55s
500:	learn: 40.0306127	test: 76.4205263	best: 76.3900308 (499)	total: 1.3s	remaining: 1.3s
600:	learn: 36.8931061	test: 76.1966209	best: 76.0565619 (567)	total: 1.58s	remaining: 1.05s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 76.05656188
bestIteration = 567

Shrink model to first 568 iterations.
0:	learn: 1337.5397339	test: 1567.8498216	best: 1567.8498216 (0)	total: 2.76ms	remaining: 2.75s
100:	learn: 107.4328007	test: 185.2805365	best: 185.2805365 (100)	total: 271ms	remaining: 2.41s
200:	learn: 60.

## 44

In [123]:
lgbm_evaluation(train_ft_44, test_ft_44)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1435.7965013	test: 1581.7750639	best: 1581.7750639 (0)	total: 4.71ms	remaining: 4.71s
100:	learn: 103.0592464	test: 156.7832594	best: 156.7832594 (100)	total: 289ms	remaining: 2.57s
200:	learn: 51.8053313	test: 113.6757695	best: 113.6055093 (178)	total: 542ms	remaining: 2.15s
300:	learn: 41.8415656	test: 113.9463674	best: 113.4903496 (207)	total: 797ms	remaining: 1.85s
400:	learn: 36.5931982	test: 113.2262406	best: 112.8998965 (377)	total: 1.06s	remaining: 1.58s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 112.8998965
bestIteration = 377

Shrink model to first 378 iterations.
0:	learn: 1433.1178511	test: 1610.4604292	best: 1610.4604292 (0)	total: 2.65ms	remaining: 2.65s
100:	learn: 103.4696281	test: 186.3903783	best: 186.3903783 (100)	total: 264ms	remaining: 2.35s
200:	learn: 51.9228689	test: 119.7539628	best: 119.7539628 (200)	total: 534ms	remaining: 2.12s
300:	learn: 41.8404948	test: 108.2839624	best: 108.1421677 (298)	total: 804ms	remaining: 1.87s
400

## 45

In [124]:
train_ft_45.head()

energy_consum  time  day  month  week  sin_time  cos_time    temp_RM  \
88704        1967.52     0    3      6    22  0.000000  1.000000  24.150000   
88705        1945.92     1    3      6    22  0.258819  0.965926  23.258333   
88706        1918.08     2    3      6    22  0.500000  0.866025  22.325000   
88707        1906.08     3    3      6    22  0.707107  0.707107  21.400000   
88708        1941.60     4    3      6    22  0.866025  0.500000  20.533333   

        wind_RM     hum_RM   temp_EMA  wind_EMA    hum_EMA        THI  \
88704  3.183333  39.666667  22.027950  2.485679  47.470422  69.672872   
88705  2.900000  43.583333  21.346727  2.226344  50.782665  68.942223   
88706  2.583333  47.916667  20.708769  1.991522  53.893024  68.121589   
88707  2.400000  52.583333  20.168959  2.023595  57.140251  67.254888   
88708  2.133333  57.000000  19.712196  2.019965  60.810982  66.367960   

       feels_temp  day_hour_mean  temp_2  periodic_avg_power_change_rate  \
88704   28.818026        2347.08  327.61                        0.022423   
88705   27.987268        2347.56  309.76                        0.026160   
88706   27.080175        2324.88  295.84                        0.025630   
88707   26.152269        2302.52  295.84                        0.023099   
88708   25.248724        2375.88  295.84                        0.025552   

       periodic_avg_power_change_rate_6  weekend  
88704                          0.004932        0  
88705                          0.005352        0  
88706                          0.005576        0  
88707                          0.005132        0  
88708                          0.006059        0

In [125]:
lgbm_evaluation(train_ft_45, test_ft_45)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 482.8999933	test: 416.0944203	best: 416.0944203 (0)	total: 2.69ms	remaining: 2.69s
100:	learn: 78.2499551	test: 99.6398677	best: 99.6398677 (100)	total: 261ms	remaining: 2.32s
200:	learn: 57.5711051	test: 97.4272584	best: 96.7238587 (142)	total: 527ms	remaining: 2.09s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 96.72385872
bestIteration = 142

Shrink model to first 143 iterations.
0:	learn: 475.0771816	test: 494.5349923	best: 494.5349923 (0)	total: 2.98ms	remaining: 2.98s
100:	learn: 76.9527919	test: 100.5622247	best: 100.5622247 (100)	total: 261ms	remaining: 2.32s
200:	learn: 56.3067033	test: 89.6201713	best: 89.5287552 (198)	total: 525ms	remaining: 2.09s
300:	learn: 48.8354524	test: 90.9002711	best: 89.2926385 (215)	total: 784ms	remaining: 1.82s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 89.2926385
bestIteration = 215

Shrink model to first 216 iterations.
0:	learn: 472.9114028	test: 516.3190633	best: 516.3190633 (0)	total: 6.7

## 46

In [126]:
lgbm_evaluation(train_ft_46, test_ft_46)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 505.1114324	test: 473.5172712	best: 473.5172712 (0)	total: 14.3ms	remaining: 14.3s
100:	learn: 93.0273921	test: 127.4563690	best: 127.1354451 (99)	total: 668ms	remaining: 5.94s
200:	learn: 71.3977398	test: 131.0659817	best: 127.1354451 (99)	total: 1.28s	remaining: 5.11s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 127.1354451
bestIteration = 99

Shrink model to first 100 iterations.
0:	learn: 493.2136521	test: 596.5349533	best: 596.5349533 (0)	total: 3.55ms	remaining: 3.55s
100:	learn: 93.1493155	test: 158.7153814	best: 158.7153814 (100)	total: 525ms	remaining: 4.67s
200:	learn: 72.7777756	test: 125.6561309	best: 125.6561309 (200)	total: 1.21s	remaining: 4.79s
300:	learn: 64.4508787	test: 122.0821495	best: 121.8718126 (293)	total: 1.86s	remaining: 4.31s
400:	learn: 58.0444678	test: 122.4475661	best: 121.4004224 (348)	total: 2.19s	remaining: 3.27s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 121.4004224
bestIteration = 348

Shrink mo

## 47

In [127]:
lgbm_evaluation(train_ft_47, test_ft_47)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 841.7569065	test: 827.8677416	best: 827.8677416 (0)	total: 3.08ms	remaining: 3.08s
100:	learn: 153.9875400	test: 283.0685838	best: 283.0685838 (100)	total: 272ms	remaining: 2.42s
200:	learn: 112.0557248	test: 273.5548603	best: 271.9986194 (134)	total: 529ms	remaining: 2.1s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 271.9986194
bestIteration = 134

Shrink model to first 135 iterations.
0:	learn: 835.8495221	test: 883.4412025	best: 883.4412025 (0)	total: 2.62ms	remaining: 2.62s
100:	learn: 153.9678828	test: 313.1587108	best: 312.7990752 (98)	total: 268ms	remaining: 2.38s
200:	learn: 115.9065424	test: 281.0412253	best: 279.0835021 (198)	total: 546ms	remaining: 2.17s
300:	learn: 100.8507486	test: 271.0043821	best: 270.8642106 (299)	total: 830ms	remaining: 1.93s
400:	learn: 88.4566098	test: 263.8818435	best: 263.5574908 (366)	total: 1.12s	remaining: 1.67s
500:	learn: 80.1842678	test: 264.5530756	best: 263.2447722 (472)	total: 1.42s	remaining: 1.41s
Stopped 

## 48

In [128]:
lgbm_evaluation(train_ft_48, test_ft_48)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 366.4296415	test: 355.5603786	best: 355.5603786 (0)	total: 4.99ms	remaining: 4.98s
100:	learn: 48.1538929	test: 48.9291486	best: 48.9291486 (100)	total: 272ms	remaining: 2.42s
200:	learn: 32.8506611	test: 54.9349974	best: 48.4544426 (105)	total: 535ms	remaining: 2.13s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 48.45444259
bestIteration = 105

Shrink model to first 106 iterations.
0:	learn: 359.1279118	test: 442.7913465	best: 442.7913465 (0)	total: 2.81ms	remaining: 2.8s
100:	learn: 48.4686762	test: 98.4835092	best: 98.4835092 (100)	total: 249ms	remaining: 2.21s
200:	learn: 33.3179554	test: 70.1190050	best: 70.1190050 (200)	total: 526ms	remaining: 2.09s
300:	learn: 27.7768941	test: 63.6985658	best: 63.6985658 (300)	total: 776ms	remaining: 1.8s
400:	learn: 24.2798452	test: 61.2830831	best: 61.2827765 (394)	total: 1.04s	remaining: 1.55s
500:	learn: 21.9567773	test: 60.5706374	best: 60.5386176 (495)	total: 1.29s	remaining: 1.28s
600:	learn: 20.3411967	test

## 49

In [129]:
lgbm_evaluation(train_ft_49, test_ft_49)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 433.5073274	test: 399.1032851	best: 399.1032851 (0)	total: 4.22ms	remaining: 4.22s
100:	learn: 68.5901856	test: 112.6390894	best: 112.6390894 (100)	total: 519ms	remaining: 4.62s
200:	learn: 49.1375433	test: 104.4236344	best: 104.4236344 (200)	total: 1.1s	remaining: 4.38s
300:	learn: 41.9431041	test: 100.6419284	best: 100.6175144 (298)	total: 1.76s	remaining: 4.09s
400:	learn: 37.0800868	test: 99.0259816	best: 99.0259816 (400)	total: 2.35s	remaining: 3.52s
500:	learn: 33.4819012	test: 98.3212852	best: 98.3156877 (498)	total: 2.61s	remaining: 2.6s
600:	learn: 31.1162713	test: 97.7653194	best: 97.7222945 (581)	total: 2.86s	remaining: 1.9s
700:	learn: 29.2137688	test: 97.2070735	best: 97.2022445 (699)	total: 3.13s	remaining: 1.33s
800:	learn: 27.6254932	test: 97.0013736	best: 96.9286530 (747)	total: 3.39s	remaining: 843ms
900:	learn: 26.3171913	test: 96.9855455	best: 96.8399913 (875)	total: 3.64s	remaining: 400ms
999:	learn: 24.9851387	test: 96.5857707	best: 96.5857707 (999)	tota

## 50

In [130]:
lgbm_evaluation(train_ft_50, test_ft_50)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 433.1949406	test: 371.8590614	best: 371.8590614 (0)	total: 4.23ms	remaining: 4.22s
100:	learn: 62.2420156	test: 93.5183453	best: 93.5183453 (100)	total: 639ms	remaining: 5.68s
200:	learn: 44.6704503	test: 90.8357233	best: 89.7775068 (156)	total: 1.27s	remaining: 5.04s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 89.7775068
bestIteration = 156

Shrink model to first 157 iterations.
0:	learn: 426.4250682	test: 459.4276839	best: 459.4276839 (0)	total: 3ms	remaining: 3s
100:	learn: 62.4543073	test: 136.4341928	best: 136.4341928 (100)	total: 268ms	remaining: 2.39s
200:	learn: 44.4618190	test: 103.8767877	best: 103.8767877 (200)	total: 527ms	remaining: 2.1s
300:	learn: 38.4723909	test: 96.2193508	best: 96.2193508 (300)	total: 794ms	remaining: 1.84s
400:	learn: 34.0649103	test: 92.7836426	best: 92.7836426 (400)	total: 1.05s	remaining: 1.57s
500:	learn: 31.0492969	test: 90.5123802	best: 90.4999071 (496)	total: 1.32s	remaining: 1.32s
600:	learn: 28.7968277	test: 

## 51

In [131]:
lgbm_evaluation(train_ft_51, test_ft_51)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 486.7810760	test: 403.0462605	best: 403.0462605 (0)	total: 2.87ms	remaining: 2.87s
100:	learn: 81.5007314	test: 91.4903343	best: 91.4903343 (100)	total: 271ms	remaining: 2.41s
200:	learn: 59.9863921	test: 97.2963701	best: 91.4903343 (100)	total: 538ms	remaining: 2.14s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 91.49033434
bestIteration = 100

Shrink model to first 101 iterations.
0:	learn: 474.6969531	test: 544.5459457	best: 544.5459457 (0)	total: 7.7ms	remaining: 7.7s
100:	learn: 80.7666115	test: 151.4144051	best: 151.4144051 (100)	total: 651ms	remaining: 5.79s
200:	learn: 59.4674656	test: 120.0459996	best: 119.8866199 (197)	total: 1.33s	remaining: 5.28s
300:	learn: 51.8642120	test: 116.6207371	best: 116.3166588 (275)	total: 1.78s	remaining: 4.13s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 116.3166588
bestIteration = 275

Shrink model to first 276 iterations.
0:	learn: 480.1022077	test: 478.1416317	best: 478.1416317 (0)	total: 

## 52

In [132]:
lgbm_evaluation(train_ft_52, test_ft_52)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 484.3237667	test: 420.6608500	best: 420.6608500 (0)	total: 7.49ms	remaining: 7.48s
100:	learn: 69.7113413	test: 93.2999217	best: 93.2999217 (100)	total: 272ms	remaining: 2.42s
200:	learn: 53.4992392	test: 84.7539722	best: 84.7372025 (187)	total: 520ms	remaining: 2.07s
300:	learn: 47.5510280	test: 85.4572578	best: 84.6947858 (202)	total: 792ms	remaining: 1.84s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 84.69478576
bestIteration = 202

Shrink model to first 203 iterations.
0:	learn: 479.0752092	test: 477.7932249	best: 477.7932249 (0)	total: 3.09ms	remaining: 3.09s
100:	learn: 70.1387540	test: 69.7694332	best: 69.7694332 (100)	total: 251ms	remaining: 2.23s
200:	learn: 53.1670609	test: 64.0816933	best: 63.8243999 (169)	total: 521ms	remaining: 2.07s
300:	learn: 47.1373343	test: 64.3203068	best: 63.7389482 (244)	total: 790ms	remaining: 1.83s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 63.73894823
bestIteration = 244

Shrink model to fi

## 53

In [133]:
lgbm_evaluation(train_ft_53, test_ft_53)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 990.2143893	test: 911.5529760	best: 911.5529760 (0)	total: 4.47ms	remaining: 4.47s
100:	learn: 148.9381525	test: 277.2295154	best: 277.2295154 (100)	total: 274ms	remaining: 2.44s
200:	learn: 111.8254000	test: 283.7804066	best: 274.0782580 (118)	total: 540ms	remaining: 2.15s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 274.078258
bestIteration = 118

Shrink model to first 119 iterations.
0:	learn: 980.7216907	test: 1017.0663718	best: 1017.0663718 (0)	total: 1.37ms	remaining: 1.37s
100:	learn: 151.2250071	test: 177.2971525	best: 177.2971525 (100)	total: 269ms	remaining: 2.39s
200:	learn: 113.2094330	test: 184.9492940	best: 175.3156240 (121)	total: 555ms	remaining: 2.2s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 175.315624
bestIteration = 121

Shrink model to first 122 iterations.
0:	learn: 974.3566501	test: 1089.8679447	best: 1089.8679447 (0)	total: 2.72ms	remaining: 2.71s
100:	learn: 149.3443546	test: 257.1308640	best: 257.1308640 

## 54

In [134]:
lgbm_evaluation(train_ft_54, test_ft_54)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 990.3358168	test: 799.7750772	best: 799.7750772 (0)	total: 8.71ms	remaining: 8.7s
100:	learn: 144.7396887	test: 328.2290100	best: 327.6295737 (92)	total: 283ms	remaining: 2.52s
200:	learn: 108.5630758	test: 343.8341387	best: 327.6295737 (92)	total: 548ms	remaining: 2.18s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 327.6295737
bestIteration = 92

Shrink model to first 93 iterations.
0:	learn: 959.3439168	test: 1158.1668052	best: 1158.1668052 (0)	total: 2.56ms	remaining: 2.56s
100:	learn: 146.8586029	test: 231.6657908	best: 231.6657908 (100)	total: 258ms	remaining: 2.3s
200:	learn: 111.1279176	test: 191.9011335	best: 191.9011335 (200)	total: 514ms	remaining: 2.04s
300:	learn: 98.0043702	test: 187.8124521	best: 187.5282283 (295)	total: 771ms	remaining: 1.79s
400:	learn: 89.5569103	test: 187.1984340	best: 186.3491656 (352)	total: 1.04s	remaining: 1.55s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 186.3491656
bestIteration = 352

Shrink

## 55

In [135]:
lgbm_evaluation(train_ft_55, test_ft_55)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 72.1126698	test: 62.7604673	best: 62.7604673 (0)	total: 4.06ms	remaining: 4.06s
100:	learn: 11.6477896	test: 18.2222552	best: 18.1569565 (91)	total: 263ms	remaining: 2.34s
200:	learn: 9.0309307	test: 19.1640242	best: 18.0744022 (104)	total: 513ms	remaining: 2.04s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 18.07440219
bestIteration = 104

Shrink model to first 105 iterations.
0:	learn: 70.3222557	test: 82.7808544	best: 82.7808544 (0)	total: 2.78ms	remaining: 2.77s
100:	learn: 11.6101360	test: 20.5664938	best: 20.5664938 (100)	total: 264ms	remaining: 2.35s
200:	learn: 9.0233357	test: 16.6228726	best: 16.6228726 (200)	total: 519ms	remaining: 2.06s
300:	learn: 8.0384949	test: 15.9387636	best: 15.9296397 (296)	total: 781ms	remaining: 1.81s
400:	learn: 7.2351611	test: 15.5529813	best: 15.5515104 (399)	total: 1.05s	remaining: 1.57s
500:	learn: 6.7485060	test: 15.5297767	best: 15.5288076 (496)	total: 1.31s	remaining: 1.3s
600:	learn: 6.3213880	test: 15.5417927

## 56

In [136]:
lgbm_evaluation(train_ft_56, test_ft_56)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 180.0568135	test: 147.9934887	best: 147.9934887 (0)	total: 8.99ms	remaining: 8.98s
100:	learn: 28.6518359	test: 46.2921860	best: 46.2708878 (99)	total: 299ms	remaining: 2.66s
200:	learn: 19.7095930	test: 46.7004187	best: 45.7612577 (119)	total: 935ms	remaining: 3.71s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 45.7612577
bestIteration = 119

Shrink model to first 120 iterations.
0:	learn: 177.9931572	test: 168.5739947	best: 168.5739947 (0)	total: 4.97ms	remaining: 4.96s
100:	learn: 29.0407624	test: 31.9089718	best: 31.8646158 (99)	total: 559ms	remaining: 4.98s
200:	learn: 20.7496228	test: 30.1496015	best: 29.9945219 (185)	total: 1.2s	remaining: 4.78s
300:	learn: 17.7177358	test: 28.9758539	best: 28.9461780 (296)	total: 1.81s	remaining: 4.21s
400:	learn: 15.7343869	test: 28.9293530	best: 28.8279848 (359)	total: 2.38s	remaining: 3.56s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 28.8279848
bestIteration = 359

Shrink model to first 3

## 57

In [137]:
lgbm_evaluation(train_ft_57, test_ft_57)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 747.5513637	test: 792.7385334	best: 792.7385334 (0)	total: 6.66ms	remaining: 6.65s
100:	learn: 89.9570122	test: 136.7528997	best: 136.7528997 (100)	total: 281ms	remaining: 2.5s
200:	learn: 65.8342137	test: 126.7335429	best: 125.4452244 (147)	total: 542ms	remaining: 2.15s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 125.4452244
bestIteration = 147

Shrink model to first 148 iterations.
0:	learn: 745.2952091	test: 817.7693967	best: 817.7693967 (0)	total: 2.82ms	remaining: 2.82s
100:	learn: 93.4652927	test: 123.0216776	best: 123.0216776 (100)	total: 257ms	remaining: 2.29s
200:	learn: 70.2522051	test: 101.0880181	best: 101.0880181 (200)	total: 529ms	remaining: 2.1s
300:	learn: 61.8666342	test: 99.6950486	best: 98.8283217 (266)	total: 789ms	remaining: 1.83s
400:	learn: 54.9776950	test: 100.8633660	best: 98.6202394 (340)	total: 1.04s	remaining: 1.56s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 98.62023935
bestIteration = 340

Shrink mode

## 58

In [138]:
lgbm_evaluation(train_ft_58, test_ft_58)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 62.0679879	test: 45.7200564	best: 45.7200564 (0)	total: 2.75ms	remaining: 2.74s
100:	learn: 13.4875210	test: 17.9924298	best: 17.9924298 (100)	total: 257ms	remaining: 2.29s
200:	learn: 10.5610159	test: 18.6214329	best: 17.9667951 (102)	total: 520ms	remaining: 2.07s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 17.96679507
bestIteration = 102

Shrink model to first 103 iterations.
0:	learn: 60.4793207	test: 65.3163619	best: 65.3163619 (0)	total: 2.81ms	remaining: 2.81s
100:	learn: 13.4751134	test: 17.9951996	best: 17.9951996 (100)	total: 262ms	remaining: 2.33s
200:	learn: 10.5599272	test: 14.0311874	best: 14.0311874 (200)	total: 534ms	remaining: 2.12s
300:	learn: 9.3979505	test: 13.4071291	best: 13.4071291 (300)	total: 793ms	remaining: 1.84s
400:	learn: 8.5954121	test: 13.2829581	best: 13.2252585 (377)	total: 1.07s	remaining: 1.6s
500:	learn: 8.0912055	test: 13.1615710	best: 13.1615710 (500)	total: 1.33s	remaining: 1.32s
600:	learn: 7.6052520	test: 13.0799

## 59

In [139]:
lgbm_evaluation(train_ft_59, test_ft_59)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 868.5195082	test: 801.1304952	best: 801.1304952 (0)	total: 2.92ms	remaining: 2.91s
100:	learn: 93.9458733	test: 190.0177476	best: 190.0177476 (100)	total: 259ms	remaining: 2.31s
200:	learn: 66.8156543	test: 186.8660733	best: 185.4675409 (158)	total: 536ms	remaining: 2.13s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 185.4675409
bestIteration = 158

Shrink model to first 159 iterations.
0:	learn: 857.5328981	test: 950.8882321	best: 950.8882321 (0)	total: 2.67ms	remaining: 2.66s
100:	learn: 94.2287770	test: 132.9288839	best: 132.9288839 (100)	total: 268ms	remaining: 2.38s
200:	learn: 66.1677093	test: 107.1041035	best: 107.0855392 (199)	total: 541ms	remaining: 2.15s
300:	learn: 59.2870744	test: 103.5749831	best: 103.4668755 (280)	total: 815ms	remaining: 1.89s
400:	learn: 53.4699598	test: 101.5193375	best: 101.4411930 (399)	total: 1.08s	remaining: 1.61s
500:	learn: 49.4384750	test: 100.7470472	best: 100.5782479 (490)	total: 1.35s	remaining: 1.35s
600:	learn:

## 60

In [140]:
lgbm_evaluation(train_ft_60, test_ft_60)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 997.4059675	test: 906.2766995	best: 906.2766995 (0)	total: 9.03ms	remaining: 9.02s
100:	learn: 127.1389782	test: 229.3056595	best: 229.3056595 (100)	total: 683ms	remaining: 6.08s
200:	learn: 94.1597556	test: 222.1936036	best: 221.4082332 (148)	total: 1.35s	remaining: 5.38s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 221.4082332
bestIteration = 148

Shrink model to first 149 iterations.
0:	learn: 984.7473960	test: 1042.5144575	best: 1042.5144575 (0)	total: 3.34ms	remaining: 3.33s
100:	learn: 133.0224031	test: 157.8440801	best: 157.8440801 (100)	total: 691ms	remaining: 6.15s
200:	learn: 98.0975231	test: 133.3447350	best: 133.3447350 (200)	total: 1.07s	remaining: 4.25s
300:	learn: 86.6417921	test: 137.0794599	best: 133.0360565 (216)	total: 1.33s	remaining: 3.1s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 133.0360565
bestIteration = 216

Shrink model to first 217 iterations.
0:	learn: 982.9834792	test: 1056.2656182	best: 1056.2656182 

## 61

In [141]:
lgbm_evaluation(train_ft_61, test_ft_61)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 748.1711796	test: 680.5648199	best: 680.5648199 (0)	total: 4.03ms	remaining: 4.03s
100:	learn: 145.3380035	test: 158.3848923	best: 158.3848923 (100)	total: 265ms	remaining: 2.36s
200:	learn: 101.1477655	test: 152.4508521	best: 151.1414986 (175)	total: 607ms	remaining: 2.41s
300:	learn: 82.7078826	test: 150.7697966	best: 150.3133430 (267)	total: 890ms	remaining: 2.07s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 150.313343
bestIteration = 267

Shrink model to first 268 iterations.
0:	learn: 721.6041559	test: 985.2408584	best: 985.2408584 (0)	total: 2.86ms	remaining: 2.86s
100:	learn: 146.9753118	test: 264.5587222	best: 264.5587222 (100)	total: 265ms	remaining: 2.36s
200:	learn: 104.2179592	test: 174.6852880	best: 174.6852880 (200)	total: 542ms	remaining: 2.15s
300:	learn: 83.7878415	test: 148.6216809	best: 148.5577472 (299)	total: 811ms	remaining: 1.88s
400:	learn: 71.0775227	test: 139.6624475	best: 139.6624475 (400)	total: 1.08s	remaining: 1.61s
500:	lea

## 62

In [142]:
lgbm_evaluation(train_ft_62, test_ft_62)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 295.4213278	test: 272.9474229	best: 272.9474229 (0)	total: 2.89ms	remaining: 2.88s
100:	learn: 55.8724393	test: 63.0145956	best: 63.0145956 (100)	total: 284ms	remaining: 2.53s
200:	learn: 38.3170116	test: 59.0223403	best: 59.0212126 (199)	total: 580ms	remaining: 2.31s
300:	learn: 31.1201021	test: 57.4593406	best: 57.4126805 (282)	total: 852ms	remaining: 1.98s
400:	learn: 26.4817720	test: 56.8241171	best: 56.6495799 (357)	total: 1.13s	remaining: 1.68s
500:	learn: 23.4396380	test: 55.9410723	best: 55.9201368 (498)	total: 1.4s	remaining: 1.39s
600:	learn: 21.0464749	test: 55.2676848	best: 55.2676848 (600)	total: 1.67s	remaining: 1.11s
700:	learn: 19.4244741	test: 55.1496296	best: 55.0201372 (667)	total: 1.96s	remaining: 837ms
800:	learn: 17.9725252	test: 54.9639262	best: 54.7615908 (787)	total: 2.25s	remaining: 560ms
900:	learn: 16.8578998	test: 54.5629724	best: 54.5592730 (893)	total: 2.54s	remaining: 279ms
999:	learn: 15.8475096	test: 54.4516474	best: 54.4516474 (999)	total: 2

## 63

In [143]:
lgbm_evaluation(train_ft_63, test_ft_63)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 203.4330420	test: 188.7296264	best: 188.7296264 (0)	total: 3.11ms	remaining: 3.11s
100:	learn: 42.7939733	test: 42.5547291	best: 42.5547291 (100)	total: 268ms	remaining: 2.39s
200:	learn: 27.8057443	test: 40.2298158	best: 39.6504164 (177)	total: 526ms	remaining: 2.09s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 39.6504164
bestIteration = 177

Shrink model to first 178 iterations.
0:	learn: 192.5064650	test: 315.2832474	best: 315.2832474 (0)	total: 2.65ms	remaining: 2.64s
100:	learn: 41.1072747	test: 116.1796803	best: 116.1796803 (100)	total: 277ms	remaining: 2.46s
200:	learn: 27.0727746	test: 95.7728673	best: 95.7109088 (198)	total: 541ms	remaining: 2.15s
300:	learn: 21.5546842	test: 84.6084719	best: 84.4543980 (299)	total: 797ms	remaining: 1.85s
400:	learn: 18.4116862	test: 79.2023586	best: 79.2023586 (400)	total: 1.08s	remaining: 1.61s
500:	learn: 16.2953322	test: 77.0106068	best: 76.9764959 (498)	total: 1.34s	remaining: 1.33s
600:	learn: 14.6970663	t

## 64

In [144]:
lgbm_evaluation(train_ft_64, test_ft_64)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 260.8512368	test: 231.6434169	best: 231.6434169 (0)	total: 3.5ms	remaining: 3.49s
100:	learn: 48.0672329	test: 44.7173301	best: 44.7173301 (100)	total: 256ms	remaining: 2.28s
200:	learn: 32.4987696	test: 45.1838122	best: 44.0574391 (140)	total: 523ms	remaining: 2.08s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 44.0574391
bestIteration = 140

Shrink model to first 141 iterations.
0:	learn: 248.5775754	test: 382.1285177	best: 382.1285177 (0)	total: 2.79ms	remaining: 2.79s
100:	learn: 47.9779605	test: 106.9968402	best: 106.9968402 (100)	total: 260ms	remaining: 2.31s
200:	learn: 32.6599386	test: 77.1288859	best: 77.1288859 (200)	total: 533ms	remaining: 2.12s
300:	learn: 26.8667029	test: 69.9559013	best: 69.9559013 (300)	total: 793ms	remaining: 1.84s
400:	learn: 23.4673628	test: 68.5387914	best: 68.3350492 (352)	total: 1.07s	remaining: 1.61s
500:	learn: 20.6157333	test: 67.2849088	best: 66.8139130 (484)	total: 1.34s	remaining: 1.33s
600:	learn: 18.5994801	te

## 65

In [145]:
lgbm_evaluation(train_ft_65, test_ft_65)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 183.3153163	test: 258.7884920	best: 258.7884920 (0)	total: 5.83ms	remaining: 5.82s
100:	learn: 46.0492352	test: 73.7502716	best: 73.7502716 (100)	total: 278ms	remaining: 2.47s
200:	learn: 35.2262445	test: 65.3687992	best: 65.3687992 (200)	total: 541ms	remaining: 2.15s
300:	learn: 31.2622950	test: 63.2688419	best: 63.2688419 (300)	total: 789ms	remaining: 1.83s
400:	learn: 28.1065354	test: 63.1699053	best: 62.9655987 (343)	total: 1.06s	remaining: 1.58s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 62.96559866
bestIteration = 343

Shrink model to first 344 iterations.
0:	learn: 177.6521288	test: 323.8403275	best: 323.8403275 (0)	total: 2.82ms	remaining: 2.82s
100:	learn: 45.4682146	test: 97.1331471	best: 97.1331471 (100)	total: 271ms	remaining: 2.41s
200:	learn: 35.2059844	test: 76.0887050	best: 76.0621114 (198)	total: 527ms	remaining: 2.09s
300:	learn: 31.0513495	test: 70.8951902	best: 70.8643033 (294)	total: 808ms	remaining: 1.88s
400:	learn: 28.1707043	te

## 66

In [146]:
lgbm_evaluation(train_ft_66, test_ft_66)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 60.2585946	test: 61.0727203	best: 61.0727203 (0)	total: 6.8ms	remaining: 6.8s
100:	learn: 14.5287793	test: 14.2679459	best: 14.2679459 (100)	total: 260ms	remaining: 2.32s
200:	learn: 9.6049941	test: 14.3667693	best: 13.7274294 (120)	total: 516ms	remaining: 2.05s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 13.72742943
bestIteration = 120

Shrink model to first 121 iterations.
0:	learn: 57.2625766	test: 95.8057533	best: 95.8057533 (0)	total: 3.27ms	remaining: 3.27s
100:	learn: 13.8568318	test: 35.4719738	best: 35.4719738 (100)	total: 268ms	remaining: 2.38s
200:	learn: 9.3834607	test: 29.7503716	best: 29.7503716 (200)	total: 525ms	remaining: 2.09s
300:	learn: 7.6779215	test: 27.1444963	best: 27.1444963 (300)	total: 787ms	remaining: 1.83s
400:	learn: 6.7032422	test: 26.5671686	best: 26.5671686 (400)	total: 1.06s	remaining: 1.58s
500:	learn: 6.0405837	test: 26.1060928	best: 26.0475943 (477)	total: 1.33s	remaining: 1.32s
600:	learn: 5.5417796	test: 25.6310929

## 67

In [147]:
lgbm_evaluation(train_ft_67, test_ft_67)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 269.6273292	test: 359.8907751	best: 359.8907751 (0)	total: 7.23ms	remaining: 7.22s
100:	learn: 51.4568632	test: 89.7976509	best: 89.7976509 (100)	total: 436ms	remaining: 3.88s
200:	learn: 35.0873148	test: 87.5757361	best: 87.3678810 (198)	total: 1.06s	remaining: 4.2s
300:	learn: 28.8281657	test: 86.5248493	best: 86.3294512 (292)	total: 1.6s	remaining: 3.71s
400:	learn: 25.2039998	test: 86.3015887	best: 86.1430018 (358)	total: 2.27s	remaining: 3.38s
500:	learn: 22.4869882	test: 86.0162487	best: 85.5741863 (461)	total: 2.77s	remaining: 2.76s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 85.57418635
bestIteration = 461

Shrink model to first 462 iterations.
0:	learn: 256.6468888	test: 509.6658632	best: 509.6658632 (0)	total: 5.76ms	remaining: 5.75s
100:	learn: 48.8537875	test: 200.0032595	best: 200.0032595 (100)	total: 656ms	remaining: 5.83s
200:	learn: 34.0450761	test: 146.9951921	best: 146.9951921 (200)	total: 1.33s	remaining: 5.3s
300:	learn: 28.2429586	t

## 68

In [148]:
lgbm_evaluation(train_ft_68, test_ft_68)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 462.6706187	test: 432.5853970	best: 432.5853970 (0)	total: 6.79ms	remaining: 6.78s
100:	learn: 87.0212638	test: 82.4958903	best: 82.4958903 (100)	total: 272ms	remaining: 2.42s
200:	learn: 58.8088445	test: 85.6975432	best: 82.4958903 (100)	total: 533ms	remaining: 2.12s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 82.49589028
bestIteration = 100

Shrink model to first 101 iterations.
0:	learn: 444.5825166	test: 649.2915772	best: 649.2915772 (0)	total: 2.9ms	remaining: 2.9s
100:	learn: 87.6639601	test: 204.5387370	best: 204.5387370 (100)	total: 271ms	remaining: 2.42s
200:	learn: 59.4030703	test: 135.6402246	best: 135.6402246 (200)	total: 552ms	remaining: 2.19s
300:	learn: 48.4100265	test: 122.3393007	best: 122.3393007 (300)	total: 906ms	remaining: 2.1s
400:	learn: 40.7905390	test: 111.1745136	best: 111.1745136 (400)	total: 1.56s	remaining: 2.33s
500:	learn: 35.5312622	test: 104.9829703	best: 104.9829703 (500)	total: 2.19s	remaining: 2.18s
600:	learn: 32.263

## 69

In [149]:
lgbm_evaluation(train_ft_69, test_ft_69)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 851.8100781	test: 785.3347916	best: 785.3347916 (0)	total: 6.34ms	remaining: 6.33s
100:	learn: 109.0111391	test: 214.0318535	best: 214.0318535 (100)	total: 281ms	remaining: 2.5s
200:	learn: 75.5505063	test: 199.0100432	best: 198.8235209 (195)	total: 551ms	remaining: 2.19s
300:	learn: 66.2349842	test: 196.6932793	best: 196.6251690 (288)	total: 807ms	remaining: 1.87s
400:	learn: 59.6082154	test: 196.1003647	best: 195.9634177 (399)	total: 1.08s	remaining: 1.62s
500:	learn: 55.2666693	test: 195.5999480	best: 195.5854988 (497)	total: 1.35s	remaining: 1.34s
600:	learn: 51.6317754	test: 195.6062926	best: 195.5294251 (574)	total: 1.6s	remaining: 1.06s
700:	learn: 48.4790785	test: 194.7055165	best: 194.5979133 (685)	total: 1.86s	remaining: 795ms
800:	learn: 45.6302588	test: 195.0808339	best: 194.4747435 (720)	total: 2.14s	remaining: 533ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 194.4747435
bestIteration = 720

Shrink model to first 721 iterations.
0:	learn: 

## 70

In [150]:
lgbm_evaluation(train_ft_70, test_ft_70)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1129.3820550	test: 1013.2679655	best: 1013.2679655 (0)	total: 8.85ms	remaining: 8.84s
100:	learn: 199.0463505	test: 250.2999140	best: 250.2999140 (100)	total: 278ms	remaining: 2.47s
200:	learn: 130.7825948	test: 232.6266769	best: 232.1838420 (182)	total: 549ms	remaining: 2.18s
300:	learn: 104.1274397	test: 233.2466877	best: 231.6252367 (257)	total: 810ms	remaining: 1.88s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 231.6252367
bestIteration = 257

Shrink model to first 258 iterations.
0:	learn: 1106.9667031	test: 1233.6629498	best: 1233.6629498 (0)	total: 2.79ms	remaining: 2.78s
100:	learn: 200.5063099	test: 520.0771840	best: 513.5202078 (95)	total: 266ms	remaining: 2.37s
200:	learn: 139.4480967	test: 468.6031785	best: 452.1392089 (183)	total: 537ms	remaining: 2.13s
300:	learn: 108.1580115	test: 424.7515075	best: 421.8733231 (294)	total: 799ms	remaining: 1.86s
400:	learn: 93.7415634	test: 421.4727096	best: 417.8077673 (380)	total: 1.07s	remaining: 1.59s


## 71

In [151]:
lgbm_evaluation(train_ft_71, test_ft_71)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 363.5516503	test: 339.5087843	best: 339.5087843 (0)	total: 7ms	remaining: 7s
100:	learn: 96.2523844	test: 154.4525901	best: 154.4525901 (100)	total: 269ms	remaining: 2.4s
200:	learn: 70.8482564	test: 142.3250404	best: 142.3250404 (200)	total: 551ms	remaining: 2.19s
300:	learn: 61.0295561	test: 141.7364223	best: 141.1221249 (294)	total: 818ms	remaining: 1.9s
400:	learn: 54.7999232	test: 146.1235684	best: 141.1221249 (294)	total: 1.09s	remaining: 1.63s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 141.1221249
bestIteration = 294

Shrink model to first 295 iterations.
0:	learn: 356.6898575	test: 419.8643465	best: 419.8643465 (0)	total: 2.98ms	remaining: 2.98s
100:	learn: 95.6107985	test: 126.5663562	best: 126.5663562 (100)	total: 256ms	remaining: 2.27s
200:	learn: 71.9076795	test: 101.4162705	best: 101.4162705 (200)	total: 526ms	remaining: 2.09s
300:	learn: 61.5773275	test: 96.5090657	best: 96.2928375 (290)	total: 791ms	remaining: 1.84s
400:	learn: 55.553266

## 72

In [ ]:
lgbm_evaluation(train_ft_72, test_ft_72)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 149.8490673	test: 144.5022154	best: 144.5022154 (0)	total: 9.25ms	remaining: 9.24s
100:	learn: 28.6359662	test: 104.2864538	best: 102.1937880 (60)	total: 695ms	remaining: 6.18s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 102.193788
bestIteration = 60

Shrink model to first 61 iterations.
0:	learn: 141.0829174	test: 252.8237874	best: 252.8237874 (0)	total: 3.59ms	remaining: 3.59s
100:	learn: 29.0662521	test: 132.8044693	best: 132.8044693 (100)	total: 602ms	remaining: 5.36s
200:	learn: 21.3854325	test: 129.1258717	best: 127.8540903 (155)	total: 1.33s	remaining: 5.3s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 127.8540903
bestIteration = 155

Shrink model to first 156 iterations.
0:	learn: 148.9030789	test: 154.6285990	best: 154.6285990 (0)	total: 5.93ms	remaining: 5.92s
100:	learn: 31.0742278	test: 52.1016761	best: 49.6523093 (66)	total: 670ms	remaining: 5.96s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 49.652

## 73

In [ ]:
lgbm_evaluation(train_ft_73, test_ft_73)

## 74

In [ ]:
lgbm_evaluation(train_ft_74, test_ft_74)

## 75

In [ ]:
lgbm_evaluation(train_ft_75, test_ft_75)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 249.8027118	test: 233.7462443	best: 233.7462443 (0)	total: 6.36ms	remaining: 6.36s
100:	learn: 82.5760535	test: 67.0181652	best: 67.0181652 (100)	total: 274ms	remaining: 2.44s
200:	learn: 68.3919489	test: 65.5390345	best: 65.4531641 (181)	total: 535ms	remaining: 2.13s
300:	learn: 60.1007748	test: 65.6025307	best: 64.9487135 (275)	total: 787ms	remaining: 1.83s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 64.94871347
bestIteration = 275

Shrink model to first 276 iterations.
0:	learn: 246.2656913	test: 274.7748264	best: 274.7748264 (0)	total: 3.08ms	remaining: 3.07s
100:	learn: 83.1323739	test: 69.6847922	best: 69.6847922 (100)	total: 274ms	remaining: 2.44s
200:	learn: 68.6288994	test: 58.8424371	best: 58.8424371 (200)	total: 536ms	remaining: 2.13s
300:	learn: 59.9823349	test: 55.4779686	best: 55.1420364 (289)	total: 822ms	remaining: 1.91s
400:	learn: 54.6551777	test: 55.4885639	best: 54.2943822 (387)	total: 1.16s	remaining: 1.73s
500:	learn: 50.2717741	te

## 76

In [ ]:
lgbm_evaluation(train_ft_76, test_ft_76)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 184.2755208	test: 154.9476028	best: 154.9476028 (0)	total: 2.81ms	remaining: 2.8s
100:	learn: 43.4169907	test: 60.1979817	best: 60.1979817 (100)	total: 295ms	remaining: 2.63s
200:	learn: 33.6825576	test: 57.4336220	best: 57.4336220 (200)	total: 561ms	remaining: 2.23s
300:	learn: 29.0514941	test: 57.9797339	best: 57.1190580 (223)	total: 820ms	remaining: 1.9s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 57.11905796
bestIteration = 223

Shrink model to first 224 iterations.
0:	learn: 179.9050625	test: 204.2850501	best: 204.2850501 (0)	total: 2.73ms	remaining: 2.72s
100:	learn: 42.5202325	test: 61.4450536	best: 61.4450536 (100)	total: 262ms	remaining: 2.33s
200:	learn: 32.6489771	test: 59.7008956	best: 59.5240333 (160)	total: 522ms	remaining: 2.08s
300:	learn: 28.2377274	test: 59.4185248	best: 58.8072048 (276)	total: 776ms	remaining: 1.8s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 58.80720484
bestIteration = 276

Shrink model to first

## 77

In [ ]:
lgbm_evaluation(train_ft_77, test_ft_77)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 408.1985011	test: 348.1957308	best: 348.1957308 (0)	total: 6.85ms	remaining: 6.84s
100:	learn: 48.1631839	test: 73.4633177	best: 73.4633177 (100)	total: 274ms	remaining: 2.44s
200:	learn: 33.9757147	test: 68.0186838	best: 68.0172464 (198)	total: 534ms	remaining: 2.12s
300:	learn: 29.8317605	test: 67.2875123	best: 67.1512502 (241)	total: 799ms	remaining: 1.85s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 67.15125023
bestIteration = 241

Shrink model to first 242 iterations.
0:	learn: 403.0969145	test: 413.6482194	best: 413.6482194 (0)	total: 2.74ms	remaining: 2.73s
100:	learn: 46.9857574	test: 53.8517793	best: 53.8517793 (100)	total: 264ms	remaining: 2.35s
200:	learn: 33.4727506	test: 46.9389387	best: 46.9348328 (199)	total: 515ms	remaining: 2.04s
300:	learn: 29.7895746	test: 45.8539991	best: 45.7962693 (289)	total: 765ms	remaining: 1.77s
400:	learn: 26.7674092	test: 44.9122761	best: 44.9122761 (400)	total: 1.03s	remaining: 1.54s
500:	learn: 24.3535464	te

## 78

In [ ]:
lgbm_evaluation(train_ft_78, test_ft_78)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 649.9360273	test: 581.8451411	best: 581.8451411 (0)	total: 4.83ms	remaining: 4.83s
100:	learn: 57.3679227	test: 96.7219969	best: 96.7219969 (100)	total: 275ms	remaining: 2.44s
200:	learn: 35.3161903	test: 91.8289163	best: 90.3316554 (151)	total: 635ms	remaining: 2.52s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 90.33165537
bestIteration = 151

Shrink model to first 152 iterations.
0:	learn: 639.3319869	test: 695.7360353	best: 695.7360353 (0)	total: 5.58ms	remaining: 5.57s
100:	learn: 56.6679638	test: 77.6025146	best: 77.6025146 (100)	total: 639ms	remaining: 5.68s
200:	learn: 35.5427807	test: 55.7871850	best: 55.7871850 (200)	total: 1.28s	remaining: 5.1s
300:	learn: 29.6503931	test: 54.4163331	best: 53.8733464 (259)	total: 1.94s	remaining: 4.5s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 53.87334642
bestIteration = 259

Shrink model to first 260 iterations.
0:	learn: 637.3963212	test: 715.9583912	best: 715.9583912 (0)	total: 5.08ms

## 79

In [ ]:
lgbm_evaluation(train_ft_79, test_ft_79)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 682.7705326	test: 591.4495096	best: 591.4495096 (0)	total: 6.16ms	remaining: 6.15s
100:	learn: 82.5658654	test: 156.0146037	best: 156.0146037 (100)	total: 275ms	remaining: 2.45s
200:	learn: 54.2811500	test: 148.2631144	best: 147.8977404 (193)	total: 520ms	remaining: 2.06s
300:	learn: 45.8560786	test: 147.2015027	best: 146.9069922 (284)	total: 775ms	remaining: 1.8s
400:	learn: 40.9167390	test: 147.6479104	best: 146.9069922 (284)	total: 1.03s	remaining: 1.53s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 146.9069922
bestIteration = 284

Shrink model to first 285 iterations.
0:	learn: 673.8686703	test: 688.4491602	best: 688.4491602 (0)	total: 3.01ms	remaining: 3.01s
100:	learn: 82.5452285	test: 103.8819821	best: 103.8819821 (100)	total: 259ms	remaining: 2.3s
200:	learn: 53.0349846	test: 87.0248581	best: 86.9305365 (184)	total: 508ms	remaining: 2.02s
300:	learn: 44.6579156	test: 86.9601230	best: 86.4941290 (243)	total: 767ms	remaining: 1.78s
Stopped by overfi

## 80

In [ ]:
lgbm_evaluation(train_ft_80, test_ft_80)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 1268.2681769	test: 1161.4543263	best: 1161.4543263 (0)	total: 4.67ms	remaining: 4.67s
100:	learn: 119.9645337	test: 212.5322001	best: 212.5322001 (100)	total: 271ms	remaining: 2.41s
200:	learn: 78.1248301	test: 210.9526888	best: 205.6057529 (128)	total: 547ms	remaining: 2.17s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 205.6057529
bestIteration = 128

Shrink model to first 129 iterations.
0:	learn: 1242.2069296	test: 1452.0330825	best: 1452.0330825 (0)	total: 2.76ms	remaining: 2.76s
100:	learn: 118.8523436	test: 232.3994645	best: 232.3994645 (100)	total: 257ms	remaining: 2.29s
200:	learn: 75.1284662	test: 231.1280791	best: 217.3206345 (145)	total: 509ms	remaining: 2.02s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 217.3206345
bestIteration = 145

Shrink model to first 146 iterations.
0:	learn: 1255.2365879	test: 1304.0410336	best: 1304.0410336 (0)	total: 2.88ms	remaining: 2.87s
100:	learn: 110.4646969	test: 243.5720893	best: 234.39

## 81

In [ ]:
lgbm_evaluation(train_ft_81, test_ft_81)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 761.4167503	test: 800.1185257	best: 800.1185257 (0)	total: 3.79ms	remaining: 3.78s
100:	learn: 69.3049431	test: 69.8936067	best: 69.8936067 (100)	total: 267ms	remaining: 2.38s
200:	learn: 44.3918004	test: 51.9248197	best: 51.9248197 (200)	total: 527ms	remaining: 2.09s
300:	learn: 39.9241622	test: 50.6740933	best: 50.6095361 (283)	total: 923ms	remaining: 2.14s
400:	learn: 36.4914793	test: 50.6649029	best: 50.4631413 (353)	total: 1.57s	remaining: 2.35s
500:	learn: 33.5800275	test: 50.3136403	best: 50.1339031 (460)	total: 2.2s	remaining: 2.19s
600:	learn: 31.6914611	test: 50.0071855	best: 50.0043789 (599)	total: 2.85s	remaining: 1.89s
700:	learn: 30.0558657	test: 49.6190624	best: 49.6190197 (699)	total: 3.39s	remaining: 1.45s
800:	learn: 28.6524753	test: 49.6892033	best: 49.6190197 (699)	total: 4.07s	remaining: 1.01s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 49.61901965
bestIteration = 699

Shrink model to first 700 iterations.
0:	learn: 757.2423399	test

## 82

In [ ]:
lgbm_evaluation(train_ft_82, test_ft_82)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 922.4098428	test: 871.6796207	best: 871.6796207 (0)	total: 6.32ms	remaining: 6.31s
100:	learn: 110.1545241	test: 176.1485030	best: 176.1485030 (100)	total: 264ms	remaining: 2.35s
200:	learn: 76.7875985	test: 160.2238670	best: 160.0778066 (197)	total: 525ms	remaining: 2.09s
300:	learn: 63.2680434	test: 168.1581088	best: 160.0778066 (197)	total: 784ms	remaining: 1.82s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 160.0778066
bestIteration = 197

Shrink model to first 198 iterations.
0:	learn: 902.2030694	test: 1067.4764997	best: 1067.4764997 (0)	total: 2.72ms	remaining: 2.72s
100:	learn: 103.8067494	test: 271.0374313	best: 269.8357036 (99)	total: 255ms	remaining: 2.27s
200:	learn: 68.5332016	test: 259.6851524	best: 254.8887699 (170)	total: 503ms	remaining: 2s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 254.8887699
bestIteration = 170

Shrink model to first 171 iterations.
0:	learn: 919.3787599	test: 902.4926600	best: 902.4926600 (0)	t

## 83

In [ ]:
lgbm_evaluation(train_ft_83, test_ft_83)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 646.8630714	test: 575.4731083	best: 575.4731083 (0)	total: 4.58ms	remaining: 4.58s
100:	learn: 60.1653888	test: 116.1264896	best: 116.1264896 (100)	total: 272ms	remaining: 2.42s
200:	learn: 40.4593038	test: 109.5110485	best: 109.3190198 (152)	total: 528ms	remaining: 2.1s
300:	learn: 34.5361274	test: 109.5441811	best: 108.7608067 (263)	total: 782ms	remaining: 1.82s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 108.7608067
bestIteration = 263

Shrink model to first 264 iterations.
0:	learn: 634.4897968	test: 708.7463786	best: 708.7463786 (0)	total: 2.71ms	remaining: 2.71s
100:	learn: 60.8268910	test: 68.0692437	best: 68.0692437 (100)	total: 266ms	remaining: 2.37s
200:	learn: 40.8512066	test: 45.3220233	best: 45.1439332 (198)	total: 521ms	remaining: 2.07s
300:	learn: 34.5807759	test: 45.3668889	best: 44.7283973 (241)	total: 780ms	remaining: 1.81s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 44.72839735
bestIteration = 241

Shrink model 

## 84

In [ ]:
lgbm_evaluation(train_ft_84, test_ft_84)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 648.7280878	test: 591.4150866	best: 591.4150866 (0)	total: 2.87ms	remaining: 2.87s
100:	learn: 64.7608650	test: 118.3165367	best: 118.3165367 (100)	total: 476ms	remaining: 4.24s
200:	learn: 39.4079112	test: 113.5843332	best: 113.4905493 (196)	total: 1.02s	remaining: 4.06s
300:	learn: 31.9945479	test: 111.0812284	best: 111.0812284 (300)	total: 1.67s	remaining: 3.87s
400:	learn: 28.1036871	test: 109.7786550	best: 109.7786550 (400)	total: 2.33s	remaining: 3.47s
500:	learn: 25.2872722	test: 109.0419093	best: 109.0332053 (499)	total: 3.01s	remaining: 3s
600:	learn: 23.3010140	test: 109.4257342	best: 108.9261867 (510)	total: 3.64s	remaining: 2.42s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 108.9261867
bestIteration = 510

Shrink model to first 511 iterations.
0:	learn: 637.0084364	test: 721.7670008	best: 721.7670008 (0)	total: 2.91ms	remaining: 2.91s
100:	learn: 68.5362814	test: 110.3167139	best: 110.3167139 (100)	total: 265ms	remaining: 2.36s
200:	learn: 41

## 85

In [ ]:
lgbm_evaluation(train_ft_85, test_ft_85)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 408.0107687	test: 393.3905352	best: 393.3905352 (0)	total: 9.06ms	remaining: 9.05s
100:	learn: 62.3171547	test: 66.8779634	best: 66.8779634 (100)	total: 656ms	remaining: 5.84s
200:	learn: 45.7494288	test: 63.2701148	best: 63.2441031 (182)	total: 1.3s	remaining: 5.19s
300:	learn: 40.7759746	test: 62.7096711	best: 62.6619323 (296)	total: 1.68s	remaining: 3.89s
400:	learn: 36.7427593	test: 62.4893545	best: 62.3623065 (349)	total: 1.93s	remaining: 2.89s
500:	learn: 33.9075627	test: 61.8113495	best: 61.8113495 (500)	total: 2.22s	remaining: 2.21s
600:	learn: 31.3293108	test: 61.6922816	best: 61.6158111 (581)	total: 2.48s	remaining: 1.64s
700:	learn: 29.5299491	test: 61.7179760	best: 61.6044396 (609)	total: 2.74s	remaining: 1.17s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 61.60443964
bestIteration = 609

Shrink model to first 610 iterations.
0:	learn: 407.4639336	test: 400.7068934	best: 400.7068934 (0)	total: 2.68ms	remaining: 2.67s
100:	learn: 61.8918914	tes

## 86

In [ ]:
lgbm_evaluation(train_ft_86, test_ft_86)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 408.3595394	test: 404.4299471	best: 404.4299471 (0)	total: 2.92ms	remaining: 2.92s
100:	learn: 45.0639178	test: 46.7863807	best: 46.7863807 (100)	total: 494ms	remaining: 4.39s
200:	learn: 29.1144104	test: 36.4461598	best: 36.4134965 (194)	total: 1.14s	remaining: 4.54s
300:	learn: 24.8686432	test: 35.2581688	best: 35.2581688 (300)	total: 1.79s	remaining: 4.16s
400:	learn: 22.0462000	test: 34.6859490	best: 34.6859490 (400)	total: 2.47s	remaining: 3.69s
500:	learn: 20.3352777	test: 34.5595110	best: 34.5203269 (436)	total: 3.16s	remaining: 3.14s
600:	learn: 19.1716774	test: 34.6862974	best: 34.3531842 (546)	total: 3.68s	remaining: 2.44s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 34.3531842
bestIteration = 546

Shrink model to first 547 iterations.
0:	learn: 402.4442563	test: 468.6171140	best: 468.6171140 (0)	total: 1.3ms	remaining: 1.3s
100:	learn: 45.3046929	test: 82.0392664	best: 82.0392664 (100)	total: 271ms	remaining: 2.41s
200:	learn: 29.3717768	test:

## 87

In [ ]:
lgbm_evaluation(train_ft_87, test_ft_87)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 550.7798240	test: 432.4886325	best: 432.4886325 (0)	total: 3.86ms	remaining: 3.86s
100:	learn: 90.2972798	test: 94.6283516	best: 94.4418557 (98)	total: 266ms	remaining: 2.37s
200:	learn: 67.6079582	test: 91.0984356	best: 91.0984356 (200)	total: 535ms	remaining: 2.13s
300:	learn: 60.8359829	test: 90.0874373	best: 90.0874373 (300)	total: 814ms	remaining: 1.89s
400:	learn: 55.5588060	test: 90.3819916	best: 89.9787304 (337)	total: 1.1s	remaining: 1.65s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 89.97873039
bestIteration = 337

Shrink model to first 338 iterations.
0:	learn: 542.1442790	test: 532.2441468	best: 532.2441468 (0)	total: 6.02ms	remaining: 6.01s
100:	learn: 89.1858431	test: 145.3551970	best: 145.3551970 (100)	total: 676ms	remaining: 6.02s
200:	learn: 67.0931543	test: 120.1499318	best: 120.1499318 (200)	total: 1.27s	remaining: 5.05s
300:	learn: 59.9350515	test: 116.5710486	best: 116.5710486 (300)	total: 1.91s	remaining: 4.44s
400:	learn: 54.741841

## 88

In [ ]:
lgbm_evaluation(train_ft_88, test_ft_88)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 551.2952950	test: 580.8231019	best: 580.8231019 (0)	total: 4.75ms	remaining: 4.74s
100:	learn: 56.5796665	test: 59.4081718	best: 59.4081718 (100)	total: 268ms	remaining: 2.39s
200:	learn: 35.6370803	test: 38.3519473	best: 38.3519473 (200)	total: 542ms	remaining: 2.15s
300:	learn: 30.0475902	test: 36.8554399	best: 36.6900292 (291)	total: 806ms	remaining: 1.87s
400:	learn: 26.9522810	test: 36.0764290	best: 36.0739375 (399)	total: 1.06s	remaining: 1.58s
500:	learn: 24.6698999	test: 35.6834081	best: 35.6729441 (496)	total: 1.33s	remaining: 1.32s
600:	learn: 23.0075736	test: 35.0943008	best: 35.0676257 (570)	total: 1.59s	remaining: 1.06s
700:	learn: 21.7179662	test: 34.9628565	best: 34.9283639 (689)	total: 1.85s	remaining: 789ms
800:	learn: 20.6019838	test: 34.7976010	best: 34.7945435 (796)	total: 2.1s	remaining: 521ms
900:	learn: 19.6107089	test: 34.9308339	best: 34.7521635 (814)	total: 2.35s	remaining: 259ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 34.7

## 89

In [ ]:
lgbm_evaluation(train_ft_89, test_ft_89)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 704.1596078	test: 757.0119818	best: 757.0119818 (0)	total: 3.65ms	remaining: 3.65s
100:	learn: 81.8938722	test: 86.9933387	best: 86.9933387 (100)	total: 262ms	remaining: 2.33s
200:	learn: 52.8963661	test: 65.9946124	best: 65.9058508 (199)	total: 523ms	remaining: 2.08s
300:	learn: 45.7548596	test: 63.6935059	best: 63.5882045 (292)	total: 785ms	remaining: 1.82s
400:	learn: 41.6437853	test: 63.0014920	best: 62.9938272 (399)	total: 1.06s	remaining: 1.59s
500:	learn: 38.8930246	test: 63.0409209	best: 62.5211906 (463)	total: 1.32s	remaining: 1.32s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 62.52119065
bestIteration = 463

Shrink model to first 464 iterations.
0:	learn: 700.6132036	test: 801.8607822	best: 801.8607822 (0)	total: 2.77ms	remaining: 2.77s
100:	learn: 80.7548345	test: 108.4876217	best: 108.4876217 (100)	total: 258ms	remaining: 2.3s
200:	learn: 54.0941359	test: 65.5083447	best: 65.5083447 (200)	total: 534ms	remaining: 2.12s
300:	learn: 45.8562253	t

## 90

In [ ]:
lgbm_evaluation(train_ft_90, test_ft_90)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 734.9830541	test: 825.2148562	best: 825.2148562 (0)	total: 1.3ms	remaining: 1.3s
100:	learn: 76.3914754	test: 114.0966829	best: 114.0966829 (100)	total: 271ms	remaining: 2.41s
200:	learn: 49.8553775	test: 87.7697259	best: 87.7697259 (200)	total: 547ms	remaining: 2.17s
300:	learn: 43.7174575	test: 87.0276100	best: 86.8295715 (295)	total: 811ms	remaining: 1.88s
400:	learn: 39.7150846	test: 86.4312144	best: 86.4230013 (398)	total: 1.08s	remaining: 1.61s
500:	learn: 36.6993542	test: 86.2605681	best: 86.2605681 (500)	total: 1.35s	remaining: 1.34s
600:	learn: 34.4000611	test: 86.0213111	best: 85.9614639 (585)	total: 1.63s	remaining: 1.08s
700:	learn: 32.2787637	test: 85.9173637	best: 85.8259735 (646)	total: 1.89s	remaining: 806ms
800:	learn: 30.7336229	test: 85.7671245	best: 85.6940522 (789)	total: 2.15s	remaining: 535ms
900:	learn: 29.3918490	test: 85.3313687	best: 85.3313687 (900)	total: 2.41s	remaining: 265ms
999:	learn: 28.3220735	test: 85.1094424	best: 85.0917742 (993)	total: 

## 91

In [ ]:
lgbm_evaluation(train_ft_91, test_ft_91)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 736.6706412	test: 765.0831003	best: 765.0831003 (0)	total: 2.98ms	remaining: 2.98s
100:	learn: 82.2482825	test: 74.7943708	best: 74.7943708 (100)	total: 257ms	remaining: 2.29s
200:	learn: 56.4140093	test: 57.0391200	best: 56.8076559 (195)	total: 514ms	remaining: 2.04s
300:	learn: 48.2377311	test: 56.4701615	best: 56.2093660 (236)	total: 780ms	remaining: 1.81s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 56.20936601
bestIteration = 236

Shrink model to first 237 iterations.
0:	learn: 732.0711345	test: 815.8823230	best: 815.8823230 (0)	total: 2.8ms	remaining: 2.8s
100:	learn: 82.4493147	test: 95.9044786	best: 95.9044786 (100)	total: 259ms	remaining: 2.3s
200:	learn: 57.1606315	test: 59.6314130	best: 59.6314130 (200)	total: 512ms	remaining: 2.04s
300:	learn: 49.0974860	test: 55.0384159	best: 55.0384159 (300)	total: 801ms	remaining: 1.86s
400:	learn: 43.0485491	test: 53.8270308	best: 53.5985966 (370)	total: 1.06s	remaining: 1.58s
500:	learn: 39.6892367	test:

## 92

In [ ]:
lgbm_evaluation(train_ft_92, test_ft_92)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 509.0922355	test: 498.7153176	best: 498.7153176 (0)	total: 2.98ms	remaining: 2.98s
100:	learn: 64.3578978	test: 69.9396454	best: 69.9396454 (100)	total: 271ms	remaining: 2.41s
200:	learn: 44.3962852	test: 55.0939700	best: 55.0674596 (199)	total: 531ms	remaining: 2.11s
300:	learn: 39.2884639	test: 53.4555982	best: 53.4490945 (299)	total: 792ms	remaining: 1.84s
400:	learn: 35.5942982	test: 53.5186938	best: 53.3271119 (322)	total: 1.05s	remaining: 1.57s
500:	learn: 32.6422491	test: 52.7526752	best: 52.7292377 (498)	total: 1.32s	remaining: 1.32s
600:	learn: 30.7309369	test: 52.3286828	best: 52.3150447 (575)	total: 1.59s	remaining: 1.05s
700:	learn: 29.0114443	test: 52.5426134	best: 52.2184835 (656)	total: 1.85s	remaining: 788ms
Stopped by overfitting detector  (120 iterations wait)

bestTest = 52.21848347
bestIteration = 656

Shrink model to first 657 iterations.
0:	learn: 510.4552664	test: 482.8354065	best: 482.8354065 (0)	total: 2.83ms	remaining: 2.83s
100:	learn: 67.0616278	te

## 93

In [ ]:
lgbm_evaluation(train_ft_93, test_ft_93)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 235.3729331	test: 171.5903223	best: 171.5903223 (0)	total: 4.36ms	remaining: 4.36s
100:	learn: 41.7451711	test: 38.5484290	best: 36.9052407 (62)	total: 281ms	remaining: 2.5s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 36.90524074
bestIteration = 62

Shrink model to first 63 iterations.
0:	learn: 233.0650816	test: 198.3877708	best: 198.3877708 (0)	total: 2.85ms	remaining: 2.85s
100:	learn: 41.0507727	test: 57.9826099	best: 57.9826099 (100)	total: 271ms	remaining: 2.42s
200:	learn: 31.7017266	test: 48.1506790	best: 48.1506790 (200)	total: 551ms	remaining: 2.19s
300:	learn: 28.0644668	test: 45.6548509	best: 45.6412058 (299)	total: 819ms	remaining: 1.9s
400:	learn: 25.3345231	test: 45.5149809	best: 45.3068918 (348)	total: 1.09s	remaining: 1.63s
500:	learn: 23.1011229	test: 44.7935576	best: 44.7604711 (496)	total: 1.37s	remaining: 1.37s
600:	learn: 21.3734599	test: 45.0507058	best: 44.7311334 (520)	total: 1.65s	remaining: 1.09s
Stopped by overfitting detecto

## 94

In [ ]:
lgbm_evaluation(train_ft_94, test_ft_94)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 552.8714707	test: 589.9576744	best: 589.9576744 (0)	total: 4.66ms	remaining: 4.66s
100:	learn: 120.6461364	test: 165.2521143	best: 165.2521143 (100)	total: 274ms	remaining: 2.44s
200:	learn: 94.9395526	test: 157.6924642	best: 156.8067130 (151)	total: 537ms	remaining: 2.14s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 156.806713
bestIteration = 151

Shrink model to first 152 iterations.
0:	learn: 548.5153173	test: 642.5269885	best: 642.5269885 (0)	total: 5.88ms	remaining: 5.88s
100:	learn: 124.3731102	test: 181.4150553	best: 181.4150553 (100)	total: 683ms	remaining: 6.08s
200:	learn: 99.1632812	test: 134.6818566	best: 134.6818566 (200)	total: 1.33s	remaining: 5.28s
300:	learn: 87.6448259	test: 130.7742283	best: 130.3372926 (293)	total: 1.98s	remaining: 4.6s
400:	learn: 78.0323914	test: 132.7430934	best: 130.3372926 (293)	total: 2.62s	remaining: 3.92s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 130.3372926
bestIteration = 293

Shrink

## 95

In [ ]:
lgbm_evaluation(train_ft_95, test_ft_95)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 249.6753554	test: 315.6005829	best: 315.6005829 (0)	total: 7.57ms	remaining: 7.56s
100:	learn: 122.1932369	test: 168.6708914	best: 168.6708914 (100)	total: 274ms	remaining: 2.44s
200:	learn: 107.9235123	test: 165.2075497	best: 164.6394965 (162)	total: 542ms	remaining: 2.16s
300:	learn: 99.1258242	test: 165.1199888	best: 164.3435501 (271)	total: 801ms	remaining: 1.86s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 164.3435501
bestIteration = 271

Shrink model to first 272 iterations.
0:	learn: 248.9952812	test: 328.3401359	best: 328.3401359 (0)	total: 2.71ms	remaining: 2.71s
100:	learn: 123.2608825	test: 164.4115685	best: 164.4115685 (100)	total: 254ms	remaining: 2.26s
200:	learn: 109.2946596	test: 150.2331505	best: 150.1682604 (196)	total: 515ms	remaining: 2.05s
300:	learn: 100.8668619	test: 146.7058051	best: 146.6324053 (298)	total: 773ms	remaining: 1.79s
400:	learn: 94.1663614	test: 146.4967460	best: 146.3454203 (351)	total: 1.03s	remaining: 1.55s
Stoppe

## 96

In [ ]:
lgbm_evaluation(train_ft_96, test_ft_96)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 574.4890576	test: 639.3265389	best: 639.3265389 (0)	total: 3.46ms	remaining: 3.46s
100:	learn: 96.5286739	test: 93.6704603	best: 93.6704603 (100)	total: 258ms	remaining: 2.29s
200:	learn: 73.5772553	test: 80.1874863	best: 80.1723108 (199)	total: 510ms	remaining: 2.03s
300:	learn: 64.9564377	test: 80.0165937	best: 79.9384537 (221)	total: 763ms	remaining: 1.77s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 79.93845371
bestIteration = 221

Shrink model to first 222 iterations.
0:	learn: 569.6224616	test: 702.0856020	best: 702.0856020 (0)	total: 2.57ms	remaining: 2.57s
100:	learn: 94.2497292	test: 129.5386858	best: 129.5386858 (100)	total: 255ms	remaining: 2.27s
200:	learn: 71.8113664	test: 104.5749950	best: 104.4983101 (198)	total: 507ms	remaining: 2.02s
300:	learn: 63.2563012	test: 100.5440866	best: 100.4387863 (299)	total: 759ms	remaining: 1.76s
400:	learn: 57.7495207	test: 98.8344102	best: 98.8344102 (400)	total: 1.03s	remaining: 1.54s
500:	learn: 52.8133

## 97

In [ ]:
lgbm_evaluation(train_ft_97, test_ft_97)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 273.1098064	test: 344.5383902	best: 344.5383902 (0)	total: 4ms	remaining: 3.99s
100:	learn: 59.0149207	test: 83.5550407	best: 83.5550407 (100)	total: 285ms	remaining: 2.53s
200:	learn: 46.1533159	test: 68.2863968	best: 68.1404814 (198)	total: 539ms	remaining: 2.14s
300:	learn: 41.0387156	test: 67.0019805	best: 66.7001157 (268)	total: 794ms	remaining: 1.84s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 66.70011574
bestIteration = 268

Shrink model to first 269 iterations.
0:	learn: 275.3118269	test: 319.4933662	best: 319.4933662 (0)	total: 2.77ms	remaining: 2.77s
100:	learn: 58.2559432	test: 59.9354850	best: 59.9354850 (100)	total: 279ms	remaining: 2.48s
200:	learn: 46.1082361	test: 57.4200241	best: 57.4175789 (199)	total: 534ms	remaining: 2.12s
300:	learn: 41.2052332	test: 56.8218315	best: 56.8218315 (300)	total: 787ms	remaining: 1.83s
400:	learn: 37.7377026	test: 56.9705793	best: 56.6540845 (349)	total: 1.04s	remaining: 1.56s
Stopped by overfitting detec

## 98

In [ ]:
lgbm_evaluation(train_ft_98, test_ft_98)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 343.5923304	test: 355.4631054	best: 355.4631054 (0)	total: 2.77ms	remaining: 2.77s
100:	learn: 77.4276926	test: 121.8588250	best: 121.8387515 (99)	total: 282ms	remaining: 2.51s
200:	learn: 62.8680007	test: 115.2588267	best: 115.2588267 (200)	total: 652ms	remaining: 2.59s
300:	learn: 56.9834630	test: 114.4778504	best: 114.3170000 (294)	total: 1.31s	remaining: 3.05s
400:	learn: 52.4568579	test: 114.3074333	best: 114.2312750 (379)	total: 1.83s	remaining: 2.74s
500:	learn: 48.5147308	test: 114.1640573	best: 114.1166081 (480)	total: 2.48s	remaining: 2.47s
600:	learn: 45.4479208	test: 115.2039840	best: 114.1166081 (480)	total: 3.16s	remaining: 2.1s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 114.1166081
bestIteration = 480

Shrink model to first 481 iterations.
0:	learn: 345.4631463	test: 333.2796694	best: 333.2796694 (0)	total: 5.9ms	remaining: 5.89s
100:	learn: 79.2600526	test: 83.6096462	best: 82.2577803 (82)	total: 704ms	remaining: 6.27s
200:	learn: 64.88

## 99

In [ ]:
lgbm_evaluation(train_ft_99, test_ft_99)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 317.9534666	test: 370.5959655	best: 370.5959655 (0)	total: 2.94ms	remaining: 2.94s
100:	learn: 43.1974559	test: 56.5799677	best: 56.5799677 (100)	total: 262ms	remaining: 2.33s
200:	learn: 29.9024386	test: 46.1074235	best: 46.1074235 (200)	total: 527ms	remaining: 2.1s
300:	learn: 26.0574576	test: 44.1823067	best: 44.1823067 (300)	total: 802ms	remaining: 1.86s
400:	learn: 23.4659352	test: 43.2746334	best: 43.2722979 (399)	total: 1.08s	remaining: 1.62s
500:	learn: 21.5306433	test: 42.7159280	best: 42.7159280 (500)	total: 1.35s	remaining: 1.34s
600:	learn: 19.9221205	test: 42.6320943	best: 42.6204006 (597)	total: 1.61s	remaining: 1.07s
700:	learn: 18.7979571	test: 42.4808053	best: 42.4446112 (659)	total: 1.87s	remaining: 798ms
800:	learn: 17.9222646	test: 42.4865059	best: 42.4385787 (747)	total: 2.14s	remaining: 531ms
900:	learn: 17.1873819	test: 42.3772669	best: 42.3772669 (900)	total: 2.39s	remaining: 262ms
999:	learn: 16.4912487	test: 42.2666099	best: 42.2405049 (982)	total: 2

## 100

In [ ]:
lgbm_evaluation(train_ft_100, test_ft_100)

  0%|          | 0/4 [00:00<?, ?it/s]

0:	learn: 263.8133814	test: 278.6820883	best: 278.6820883 (0)	total: 2.74ms	remaining: 2.74s
100:	learn: 43.6741972	test: 40.0546846	best: 40.0546846 (100)	total: 260ms	remaining: 2.31s
200:	learn: 34.3528223	test: 32.5917770	best: 32.5609589 (199)	total: 528ms	remaining: 2.1s
300:	learn: 30.5301071	test: 31.3434945	best: 31.3269593 (287)	total: 790ms	remaining: 1.83s
400:	learn: 27.6916480	test: 31.4283318	best: 31.2493537 (305)	total: 1.04s	remaining: 1.56s
Stopped by overfitting detector  (120 iterations wait)

bestTest = 31.24935366
bestIteration = 305

Shrink model to first 306 iterations.
0:	learn: 262.9774244	test: 289.1022340	best: 289.1022340 (0)	total: 2.71ms	remaining: 2.7s
100:	learn: 43.0633651	test: 46.2400499	best: 46.2400499 (100)	total: 270ms	remaining: 2.4s
200:	learn: 33.8483185	test: 39.2406957	best: 39.2406957 (200)	total: 529ms	remaining: 2.1s
300:	learn: 30.4255730	test: 37.2484522	best: 37.2484522 (300)	total: 786ms	remaining: 1.82s
400:	learn: 27.7429075	test: 

# 제출

In [ ]:
# submission = pd.read_csv(f"{DATA_PATH}sample_submission.csv")

In [ ]:
len(lgbm_preds)

NameError: ignored

In [ ]:
train_ft.columns

In [ ]:
submission.iloc[:, 1] = lgbm_preds

In [ ]:
submission.to_csv(f"{DATA_PATH}submission_cat_1.csv", index=False)

In [ ]:
submission.to_csv("submission_cat_1.csv", index=False)

In [ ]:
pd.DataFrame(smape_score_mean)

In [ ]:
train_ft_1.columns